In [170]:
import csv
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objs as go
import seaborn as sns
import warnings
import math
from datetime import datetime
from sklearn.impute import SimpleImputer
import datetime as dt
from itertools import combinations
from collections import Counter
import dash
import pickle
import jupyter_dash
import plotly.io as pio
import plotly.offline as pyo
from dash import Dash, html, dcc
warnings.filterwarnings("ignore")
plt.rcParams["figure.figsize"] = (15,6)
plt.rcParams['figure.dpi'] = 70

In [171]:
data = pd.read_csv('assets/train.csv')

In [172]:
# This is Color Map for doing RFM Analysis
color_map = {
    'Top Customer': '#636efa',
    'High Value Customer': '#ef553b',
    'Medium Value Customer': '#00cc96',
    'Low Value Customer':'#ab63fa',
    'Lost Customer':'#19d3f3',
    'NO Purchase':'#ffa15a'
}

In [173]:
# This color scheme is for plotting heatmap of Retention Analysis
heatmap_color_scheme_low = [
    (0,"#27159D"),
    (0.0001, "#0F0071"),
    (0.005,"#1B088C"),
    (0.01,"#470086"),
    (0.05,"#840AA5"),
    (0.1,"#B03089"),
    (0.2,"#D15073"),
    (0.4,"#F89641"),
    (0.6,"#F6B536"),
    (0.8,"#F4D12D"),
    (1,'#F2F222')
]

heatmap_color_scheme_high = [
    (0,"#27159D"),
    (0.00000001, "#0F0071"),
    (0.1,"#1B088C"),
    (0.2,"#470086"),
    (0.3,"#840AA5"),
    (0.5,"#B03089"),
    (0.7,"#D15073"),
    (0.9,"#F89641"),
    (1,'#F2F222')
]

In [174]:
# This functionm will return Year and Month for a data value
# Here month number 1 means January, 2 means feb as if we consider april as month 1 for numbering(only) then working changes
def get_year_int(df, column):
   year = df[column].dt.year
   month = df[column].dt.month
   return year, month

In [175]:
# This function will return quarter number for column provided
def get_quarter(x):
    if x==1 or x==2 or x==3:
        return 4
    elif x==4 or x==5 or x==6:
        return 1
    elif x==7 or x==8 or x==9:
        return 2
    elif x==10 or x==11 or x==12:
        return 3

In [176]:
# Data Dictionary to be Written in a file for creating Dashboard
main_data_dict={}
overall_dict={}
state_dict={}
product_dict={}
rfm_dict={}
ret_dict={}
segment_dict={}
cross_sell_dict={}

In [177]:

# PreProcessing of Data


In [178]:
print("Column of Data are : ")
for col in data.columns:
    print(col)


Column of Data are : 
Row ID
Order ID
Order Date
Ship Date
Ship Mode
Customer ID
Customer Name
Segment
Country
City
State
Postal Code
Region
Product ID
Category
Sub-Category
Product Name
Sales


In [179]:
# Finding the amount of Missing rows
missing_count = data.isna().sum().sort_values(ascending=[False])
missing_count.head(60)

Postal Code      11
Row ID            0
Order ID          0
Product Name      0
Sub-Category      0
Category          0
Product ID        0
Region            0
State             0
City              0
Country           0
Segment           0
Customer Name     0
Customer ID       0
Ship Mode         0
Ship Date         0
Order Date        0
Sales             0
dtype: int64

In [180]:
# Extracting only important column from out data in df which will be used for different analysis
# This need to be edited according to data provided

# Here we have remove column like ship mode and ship date
df = data[['Order ID','Product Name','Sub-Category','Category','Product ID','Region','State','City','Country','Segment','Customer Name','Customer ID','Order Date','Sales']].copy()

In [181]:
# Renaming the Columns
# Please edit the name of column as required 
# Column Name needed are :
# BillDate
# Quantity
# UnitRate
# State
# Name (Customer Name)
# PL1,PL2,PL3.... (This is for differnt product level if present in data)
# PC (For Product Category)
# OrderID
# Segment
# BasePrice (Revenue)
# ProductDetail (Detailed description of products)


In [182]:
df.rename(columns = {'Order ID':'OrderID','Order Date':'BillDate','Customer Name':'CustomerName','Category':'PL1','Sub-Category':'PL2','Sales':'BasePrice','Product Name':'ProductDetail'}, inplace = True)
df

OrderID                                      ProductDetail   
0     CA-2017-152156                  Bush Somerset Collection Bookcase  \
1     CA-2017-152156  Hon Deluxe Fabric Upholstered Stacking Chairs,...   
2     CA-2017-138688  Self-Adhesive Address Labels for Typewriters b...   
3     US-2016-108966      Bretford CR4500 Series Slim Rectangular Table   
4     US-2016-108966                     Eldon Fold 'N Roll Cart System   
...              ...                                                ...   
9795  CA-2017-125920  Cardinal HOLDit! Binder Insert Strips,Extra St...   
9796  CA-2016-128608           BIC Brite Liner Highlighters, Chisel Tip   
9797  CA-2016-128608                                        GE 30524EE4   
9798  CA-2016-128608           Anker 24W Portable Micro USB Car Charger   
9799  CA-2016-128608                SanDisk Cruzer 4 GB USB Flash Drive   

              PL2              PL1       Product ID   Region       State   
0       Bookcases        Furniture  FUR-BO-10001798    South    Kentucky  \
1          Chairs        Furniture  FUR-CH-10000454    South    Kentucky   
2          Labels  Office Supplies  OFF-LA-10000240     West  California   
3          Tables        Furniture  FUR-TA-10000577    South     Florida   
4         Storage  Office Supplies  OFF-ST-10000760    South     Florida   
...           ...              ...              ...      ...         ...   
9795      Binders  Office Supplies  OFF-BI-10003429  Central    Illinois   
9796          Art  Office Supplies  OFF-AR-10001374     East        Ohio   
9797       Phones       Technology  TEC-PH-10004977     East        Ohio   
9798       Phones       Technology  TEC-PH-10000912     East        Ohio   
9799  Accessories       Technology  TEC-AC-10000487     East        Ohio   

                 City        Country    Segment      CustomerName Customer ID   
0           Henderson  United States   Consumer       Claire Gute    CG-12520  \
1           Henderson  United States   Consumer       Claire Gute    CG-12520   
2         Los Angeles  United States  Corporate   Darrin Van Huff    DV-13045   
3     Fort Lauderdale  United States   Consumer    Sean O'Donnell    SO-20335   
4     Fort Lauderdale  United States   Consumer    Sean O'Donnell    SO-20335   
...               ...            ...        ...               ...         ...   
9795          Chicago  United States  Corporate     Sally Hughsby    SH-19975   
9796           Toledo  United States  Corporate  Cindy Schnelling    CS-12490   
9797           Toledo  United States  Corporate  Cindy Schnelling    CS-12490   
9798           Toledo  United States  Corporate  Cindy Schnelling    CS-12490   
9799           Toledo  United States  Corporate  Cindy Schnelling    CS-12490   

        BillDate  BasePrice  
0     08/11/2017   261.9600  
1     08/11/2017   731.9400  
2     12/06/2017    14.6200  
3     11/10/2016   957.5775  
4     11/10/2016    22.3680  
...          ...        ...  
9795  21/05/2017     3.7980  
9796  12/01/2016    10.3680  
9797  12/01/2016   235.1880  
9798  12/01/2016    26.3760  
9799  12/01/2016    10.3840  

[9800 rows x 14 columns]

In [183]:
# Please Specify the Column Present in df
# If Column is present the 1 else 0.
cdict= {
    "BillDate": 1,
    "Quantity": 0,
    "UnitRate": 0,
    "BillDate": 1,
    "State": 1,
    "CustomerName": 1,
    "PC":1,
    "PL":1,
    "OrderID":1,
    "Segment":1,
    "BasePrice":1,
    "ProductDetail":1,
}

In [184]:
# Checking the data type of all Columns
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9800 entries, 0 to 9799
Data columns (total 14 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   OrderID        9800 non-null   object 
 1   ProductDetail  9800 non-null   object 
 2   PL2            9800 non-null   object 
 3   PL1            9800 non-null   object 
 4   Product ID     9800 non-null   object 
 5   Region         9800 non-null   object 
 6   State          9800 non-null   object 
 7   City           9800 non-null   object 
 8   Country        9800 non-null   object 
 9   Segment        9800 non-null   object 
 10  CustomerName   9800 non-null   object 
 11  Customer ID    9800 non-null   object 
 12  BillDate       9800 non-null   object 
 13  BasePrice      9800 non-null   float64
dtypes: float64(1), object(13)
memory usage: 1.0+ MB


In [185]:
# Converting Object data type to String
# Do this if needed
if cdict['Quantity']==1:
    df['Quantity']=df['Quantity'].astype(str)
    df['Quantity'] = df['Quantity'].str.replace(',', '', regex=True)
    df['Quantity'] = df['Quantity'].astype(float)

if cdict['UnitRate']==1:
    df['UnitRate']=df['UnitRate'].astype(str)
    df['UnitRate'] = df['UnitRate'].str.replace(',', '', regex=True)
    df['UnitRate']=df['UnitRate'].astype(float)

if cdict['BasePrice']==1:
    df['BasePrice']=df['BasePrice'].astype(str)
    df['BasePrice'] = df['BasePrice'].str.replace(',', '', regex=True)
    df['BasePrice'] = df['BasePrice'].astype(float)


In [186]:
# Changing Bill Date object to datetime format
if cdict['BillDate']==1:
    df.BillDate = pd.to_datetime(df.BillDate, format="%d/%m/%Y")
    df[df['BillDate'].isna()]
    df.dropna(subset=['BillDate'], inplace=True)

In [187]:
missing_count = df.isna().sum()
print(f"Count of Missing Value :\n{missing_count}")

Count of Missing Value :
OrderID          0
ProductDetail    0
PL2              0
PL1              0
Product ID       0
Region           0
State            0
City             0
Country          0
Segment          0
CustomerName     0
Customer ID      0
BillDate         0
BasePrice        0
dtype: int64


In [188]:
# Removing the Negative Base Price Values
if cdict['BasePrice']==1:
    df = df[df.BasePrice > 0]

In [189]:
# Adding year and month column in df data
if cdict['BillDate']==1:
    df['Year'],df['Month']=get_year_int(df,'BillDate')
    df['Quarter']=df.apply(lambda x: get_quarter(x['Month']), axis=1)

In [190]:
df['Year'].unique()

array([2017, 2016, 2015, 2018])

In [191]:
# General Variable containing all years
# This will contain all the general Information needed to change according to data provided

# Using above output of differnt year fill this array
years=['2014-15','2015-16','2016-17','2017-18','2018-19']
first_years=['2014','2015','2016','2017','2018']
start_years=['14','15','16','17','18']
short_years=['14-15','15-16','16-17','17-18','18-19']

# This means that the last year data is incomplete so some plots will not be made for the last year in data
data_incomplete_year_count=1


quarters=['1','2','3','4']
full_quarters=['Quarter 1','Quarter 2','Quarter 3','Quarter 4']
months=['Apr','May','Jun','Jul','Aug','Sep','Oct','Nov','Dec','Jan','Feb','Mar']
Customer_Seg=["Top","High","Medium","Low","Lost"]
Customer_Segment=["Top Customer","High Value Customer","Medium Value Customer","Low Value Customer","Lost Customer"]


# This is variable for containig figure number of each plot
fig_num=1
main_fig_num=1


In [192]:
if cdict['BillDate']==1:
    # Creating different database for each year seperately
    for y in start_years:
        temp='df_'+str(y)
        x=int(y)+1
        exec(f"{temp}=df.loc[(df['BillDate'] >= '20{y}-04-01') & (df['BillDate'] <= '20{x}-03-31')]")

In [193]:
# Yearly Analysis
if cdict['BasePrice'] and cdict['BillDate']:
    print(1)

1


In [194]:
# Making another copy of Data for doing Yearly analysis
# For this section we will be working on ya and ya_18,ya_19,....
ya=df.copy() 
for y in start_years:
        temp='ya_'+str(y)
        temp2='df_'+str(y)
        exec(f"{temp}={temp2}.copy()")


In [195]:
# Making a data frame ya_year where total revenue of each year is present
ya_year=pd.DataFrame({'Year':[],'BasePrice':[]})
temp=0
for y in years:
    x='df_'+str(start_years[temp])
    x=eval(x).BasePrice.sum()
    ll={'Year':y,'BasePrice':x}
#     ya_year=ya_year.append(ll,ignore_index=True)
    ya_year = pd.concat([ya_year, pd.DataFrame(ll, index=[0])], ignore_index=True)
    temp=temp+1

print(ya_year)


      Year    BasePrice
0  2014-15   73931.3960
1  2015-16  468282.4991
2  2016-17  489764.6834
3  2017-18  629767.0692
4  2018-19  599791.1350


In [196]:
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num+=1;
title="Revenue of Each Year"
exec(f"{temp_fig}=go.Figure()")
exec(f"{temp_fig}=px.bar(ya_year,x='Year',y='BasePrice')")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()
# For data Transfer
fig_dict={}
fig_dict["Total"]=[eval(temp_fig),ya_year]
overall_dict[title]=fig_dict

In [197]:
main_fig_num=fig_num
print(main_fig_num)

2


In [198]:
# Creating ya_Mix dataframe containg revenue per month for each year
ya_mix=pd.DataFrame()
ind=0
for y in start_years:
    temp='ya_'+str(y)
    temp=eval(temp).groupby('Month').BasePrice.sum().to_frame(name=f'BasePrice{short_years[ind]}').reset_index()
    ind=ind+1
    if ya_mix.empty:
        ya_mix=temp
    else:
        ya_mix = pd.merge(ya_mix,temp, on='Month',how='outer').fillna(0)    
ya_mix

Month  BasePrice14-15  BasePrice15-16  BasePrice16-17  BasePrice17-18   
0       1       14205.707      18066.9576      18542.4910      43476.4740  \
1       2        4519.892      11951.4110      22978.8150      19920.9974   
2       3       55205.797      32339.3184      51165.0590      58863.4128   
3       4           0.000      27906.8550      34154.4685      38679.7670   
4       5           0.000      23644.3030      29959.5305      56656.9080   
5       6           0.000      34322.9356      23599.3740      39724.4860   
6       7           0.000      33781.5430      28608.2590      38320.7830   
7       8           0.000      27117.5365      36818.3422      30542.2003   
8       9           0.000      81623.5268      63133.6060      69193.3909   
9      10           0.000      31453.3930      31011.7375      59583.0330   
10     11           0.000      77907.6607      75249.3995      79066.4958   
11     12           0.000      68167.0585      74543.6012      95739.1210   

    BasePrice18-19  
0           0.0000  
1           0.0000  
2           0.0000  
3       35541.9101  
4       43825.9822  
5       48190.7277  
6       44825.1040  
7       62837.8480  
8       86152.8880  
9       77448.1312  
10     117938.1550  
11      83030.3888

In [199]:
title="Revenue Per Month Of Each Year"
fig_num=main_fig_num
fig_num=fig_num+1;
temp_fig='fig_'+str(fig_num)
exec(f"{temp_fig}=go.Figure()")
for y in short_years:
    temp='BasePrice'+str(y)
    exec(f"{temp_fig}.add_trace(go.Scatter(x=ya_mix['Month'], y=ya_mix[temp], mode='lines', name=f'Price{y}'))")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()

# For data Transfer
fig_dict={}
fig_dict["Year"]=[eval(temp_fig),ya_mix]
overall_dict[title]=fig_dict

In [200]:
main_fig_num=fig_num
print(main_fig_num)

3


In [201]:
# Creating ya_Mix dataframe containg revenue per month for each year
ya_quarter=pd.DataFrame()
ind=0
for y in start_years:
    temp='ya_'+str(y)
    temp=eval(temp).groupby('Quarter').BasePrice.sum().to_frame(name=f'BasePrice{short_years[ind]}').reset_index()
    ind=ind+1
    if ya_quarter.empty:
        ya_quarter=temp
    else:
        ya_quarter = pd.merge(ya_quarter,temp, on='Quarter',how='outer').fillna(0)
ya_quarter = ya_quarter.sort_values(by='Quarter', ascending=True)

ya_quarter

Quarter  BasePrice14-15  BasePrice15-16  BasePrice16-17  BasePrice17-18   
1        1           0.000      85874.0936      87713.3730     135061.1610  \
2        2           0.000     142522.6063     128560.2072     138056.3742   
3        3           0.000     177528.1122     180804.7382     234388.6498   
0        4       73931.396      62357.6870      92686.3650     122260.8842   

   BasePrice18-19  
1      127558.620  
2      193815.840  
3      278416.675  
0           0.000

In [202]:
title="Revenue Per Quarter of Each Year"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
for y in short_years:
    exec(f"{temp_fig}.add_trace(go.Scatter(x=ya_quarter['Quarter'],y=ya_quarter[f'BasePrice{y}'],name=f'BasePrice{y}'))")
exec(f"{temp_fig}.update_layout(title='Revenue Per Quarter in Each Year',title_font_size=24)")
eval(temp_fig).show()

# For data Transfer
fig_dict={}
fig_dict["Quarter"]=[eval(temp_fig),ya_quarter]
overall_dict[title]=fig_dict

In [203]:
main_fig_num=fig_num
print(main_fig_num)

4


In [204]:
# Assigning Overall Dictionary in Main_Data
main_data_dict["Overall Analysis"]=overall_dict

In [205]:
# State Analysis
if cdict['BasePrice'] and cdict['State'] and cdict['BillDate']:
    print(1)

1


In [206]:
# Making another copy of Data for doing State analysis
st=df.copy() 
for y in start_years:
    temp='st_'+str(y)
    temp2='df_'+str(y)
    exec(f"{temp}={temp2}.copy()")

In [207]:
# Dropping all the Column where state in null
st.dropna(subset=['State'], inplace=True)
for y in start_years:
    temp='st_'+str(y)
    exec(f"{temp}.dropna(subset=['State'], inplace=True)")

In [208]:
# Contain all the states name
states=st['State'].unique()

In [209]:
# Overall Revenue of each state
title="Revenue per State"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
state_sale_all=st.groupby("State").BasePrice.sum().sort_values(ascending = False).reset_index()
exec(f"{temp_fig}=px.bar(state_sale_all,x='State',y='BasePrice')")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()

# For data Transfer
fig_dict={}
fig_dict["Total"]=[eval(temp_fig),state_sale_all]
state_dict[title]=fig_dict

In [210]:
main_fig_num=fig_num
print(main_fig_num)

5


In [211]:
# State_Sale17 contain reveue of each state for year 2017-18
# Creating ya_Mix dataframe containg revenue per month for each year
state_sale_mix=pd.DataFrame()
ind=0
for y in start_years:
    temp='st_'+str(y)
    temp=eval(temp).groupby('State').BasePrice.sum().sort_values(ascending = False).to_frame(name=f'BasePrice{short_years[ind]}').reset_index()
    ind=ind+1
    if state_sale_mix.empty:
        state_sale_mix=temp
    else:
        state_sale_mix= pd.merge(state_sale_mix,temp, on='State',how='outer').fillna(0)


state_sale_mix

State  BasePrice14-15  BasePrice15-16  BasePrice16-17   
0                Florida       26082.622      10140.5585      14443.0545  \
1             California       10002.983      92413.6380      94499.8105   
2               Virginia        7738.610      18761.9600      19179.8200   
3               Kentucky        5157.510       3371.6600       8499.7700   
4               New York        5005.106      62418.9120      85325.6220   
5                  Texas        3114.332      52200.8926      37065.8264   
6             Washington        2757.892      34085.6440      14155.1640   
7               Arkansas        1859.400       4473.2800        413.6200   
8               Illinois        1683.134      16031.5270      21600.0280   
9              Louisiana        1287.260       1247.6600        844.7800   
10                  Iowa        1190.840          0.0000       1713.2000   
11              Michigan         971.496       5280.1150      16985.3630   
12        South Carolina         900.840       1429.5000       4088.1400   
13               Arizona         767.298       7527.9370      10101.0800   
14              Colorado         719.576       5817.6640       4836.6020   
15        North Carolina         566.757      13631.6550       6379.0310   
16              Missouri         535.270       1112.7600       7682.3700   
17          Pennsylvania         508.936      20373.3890      23510.9130   
18             Wisconsin         468.900       7937.4300       7039.0000   
19                  Ohio         454.784      16653.3460      13833.0750   
20             Minnesota         379.220      15675.6100       5616.1300   
21             Tennessee         377.722       3314.0140       8967.3080   
22            New Mexico         302.376        454.7560       1143.7520   
23                  Utah         280.276       2692.3320       3964.4000   
24               Georgia         162.730      10602.8700      10326.7500   
25          South Dakota         152.640          9.5100          0.0000   
26                Oregon         120.536       4569.8630       4792.5100   
27            New Jersey         115.360       4363.7100       4660.3660   
28           Mississippi         103.500       1951.6600       1049.5900   
29               Indiana          98.910       3028.6100       6729.4000   
30                Nevada          54.640       2506.5700       2007.0420   
31              Delaware           9.940       7722.6300       4500.5660   
32         Massachusetts           0.000       9932.6560       7068.9680   
33               Alabama           0.000       6657.5800       3373.4800   
34          Rhode Island           0.000       5615.5860        499.6600   
35              Maryland           0.000       4333.0500       8354.8010   
36           Connecticut           0.000       2794.0200       1677.5270   
37              Oklahoma           0.000       2639.3500       5770.4500   
38                Kansas           0.000       1340.9000        149.2000   
39         New Hampshire           0.000       1228.8200       4505.2240   
40                 Maine           0.000        617.1200        106.0800   
41               Montana           0.000        468.1480        891.9240   
42                 Idaho           0.000        465.2160       1534.9160   
43              Nebraska           0.000        388.3900        415.7700   
44               Vermont           0.000          0.0000       6792.4100   
45  District of Columbia           0.000          0.0000       2670.1900   
46               Wyoming           0.000          0.0000          0.0000   
47         West Virginia           0.000          0.0000          0.0000   
48          North Dakota           0.000          0.0000          0.0000   

    BasePrice17-18  BasePrice18-19  
0       11999.8295      25770.4675  
1      127702.6365     121687.3955  
2       18647.9100       6308.4200  
3        4718.3400      14711.1100  
4       65179.0120      88432.495

In [212]:
title="Revenue Per State of Each Year"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
for y in short_years:
    exec(f"{temp_fig}.add_trace(go.Bar(x=state_sale_mix['State'],y=state_sale_mix[f'BasePrice{y}'],name=f'BasePrice{y}'))")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()

# For data Transfer
fig_dict={}
fig_dict["Year"]=[eval(temp_fig),state_sale_mix]
state_dict[title]=fig_dict

In [213]:
main_fig_num=fig_num
print(main_fig_num)

6


In [214]:
st_all_quarter=df.groupby(['State','Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name='PriceAll').reset_index()
st_all_q_mix=pd.DataFrame()
for q in quarters:
    temp=pd.DataFrame()
    temp=st_all_quarter.loc[st_all_quarter['Quarter'] == int(q)][['State','PriceAll']]
    temp.rename(columns = {'PriceAll':f'Quarter {q}'}, inplace = True)
    if st_all_q_mix.empty:
        st_all_q_mix=temp
    else:
        st_all_q_mix= pd.merge(st_all_q_mix,temp, on='State',how='outer').fillna(0)
        
st_all_q_mix


State   Quarter 1    Quarter 2    Quarter 3   Quarter 4
0             California  93177.0290  121775.5695  163610.3370  67743.5280
1               New York  52602.9680   88188.8180  141159.4140  24409.9470
2                  Texas  30831.2576   57303.9372   51351.1892  29086.1482
3           Pennsylvania  27779.3840   44171.8570   33004.9170  11320.4920
4               Virginia  21895.4200   13393.8300   16283.6400  19063.8300
5               Illinois  19256.0900   23073.0600   22642.6940  14264.6730
6               Michigan  19029.9020   11834.6550   32448.4020  12823.1150
7                Florida  18910.6580   15252.4700   23312.9840  30960.4200
8             Washington  16982.5600   44660.7800   42759.2720  30804.2380
9             New Jersey  16478.4760    5258.8300   11451.2400   1422.4260
10               Georgia  14317.3400    7641.1100    5656.1700  20604.4900
11                  Ohio  12109.0940   14816.0240   39959.0660   8246.1660
12             Minnesota   8746.0800   13355.3700    6681.1900   1080.5100
13             Tennessee   7944.1690    6707.2430   13571.3330   2439.1280
14              Colorado   7883.3950    6503.9240   14787.8630   2666.4160
15               Arizona   7074.5780   10838.2730   15118.7260   2241.0800
16        North Carolina   6305.9550   11444.4460   26228.2810  11187.2820
17                Nevada   5691.1660    2023.1000    8901.6160    113.2200
18               Indiana   5279.8200    7557.5100   34932.2900    948.7800
19              Kentucky   4668.8600    7197.0400   17074.9000   7517.5900
20               Alabama   4175.2400    4186.2100   10574.3300    574.8600
21         Massachusetts   3764.8660   11942.1490   12246.1090    681.3100
22             Wisconsin   3255.6200    4183.6400   15455.6600   8278.5100
23           Connecticut   3100.7200    3860.2600    4591.7300   1831.6470
24  District of Columbia   2753.3400       0.0000      33.9200     77.7600
25           Mississippi   2284.3400    5257.4400    1539.3800   1690.1800
26              Maryland   2219.1300    8047.6300    7381.2420   6057.5210
27              Arkansas   2105.8800    4096.9100    3545.5400   1929.8000
28                  Utah   1987.6980    8228.1520     695.0100    309.1960
29              Delaware   1577.5600    3492.9790   17411.7300   4840.7300
30        South Carolina   1561.4000    4960.2200     999.7700    960.3200
31                 Idaho   1319.8460    1242.0800    1785.8800     34.6800
32               Vermont   1294.7500       0.0000    5325.1300   2309.4900
33              Missouri   1148.0200    4713.4800   10491.8900   5851.7600
34                Oregon   1023.5120    5687.4470    9887.7860    685.7170
35              Oklahoma   1017.3100    4172.6100    9379.9500   5113.5200
36             Louisiana   1003.0100    2065.8500    4732.8100   1329.3800
37          North Dakota    891.5300       0.0000      28.3800      0.0000
38         West Virginia    536.4800       0.0000     673.3440      0.0000
39         New Hampshire    459.1000    1358.5400    3866.0140   1608.8700
40              Nebraska    413.9800    2575.3400    4297.2400    178.3700
41               Montana    410.1040      54.2840     891.9240   4233.0400
42          Rhode Island    317.9500    3475.8100   18131.3660    599.9000
43            New Mexico    241.1600     785.3700    2625.4100   1131.5820
44                Kansas    168.1000    1494.4800     950.7200    301.0100
45                  Iowa    106.3200    1774.4300    1031.7500   1531.0600
46                 Maine    106.0800    1164.4500       0.0000      0.0000
47          South Dakota      0.0000    1137.4200      25.5000    152.6400
48               Wyoming      0.0000       0.0000    1603.1360      0.0000

In [215]:
# Here Revenue of Each State in Quarter 1 and 2 is more as in 2017-2022 data there is only Q1&Q2 data for year 2022 so some more value get added to Q1&Q2 and not in Q3&Q4
title="Revenue Per State of Each Quarter"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
for f in full_quarters:
    exec(f"{temp_fig}.add_trace(go.Bar(x=st_all_q_mix['State'],y=st_all_q_mix[f],name=f))")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()

# For data Transfer
fig_dict={}
fig_dict["Quarter"]=[eval(temp_fig),st_all_q_mix]
state_dict[title]=fig_dict


In [216]:
main_fig_num=fig_num
print(main_fig_num)

7


In [217]:
ind=0
for year in start_years:
    fetch_data='df_'+str(year)
    work_data='st_'+str(year)+'_quarter'
    exec(f"{work_data}={fetch_data}.groupby(['State','Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name=f'Price{short_years[ind]}').reset_index()")
    main_data='st_'+str(year)+'_q_mix'
    exec(f"{main_data}=pd.DataFrame()")
    
    for q in quarters:
        temp=pd.DataFrame()
        temp=eval(work_data).loc[eval(work_data)['Quarter'] == int(q)][['State',f'Price{short_years[ind]}']]
        temp.rename(columns = {f'Price{short_years[ind]}':f'Quarter {q}'}, inplace = True)
        if eval(main_data).empty:
            exec(f"{main_data}=temp")
        else:
            exec(f"{main_data}= pd.merge({main_data},temp, on='State',how='outer').fillna(0)")
    for q in full_quarters:
        if q not in eval(main_data).columns:
            exec(f"{main_data}[q] = 0")
    exec(f"{main_data}['Year']='{years[ind]}'")
    print(f"\n\n Year : {years[ind]}")
    ind=ind+1
    print(eval(main_data))




 Year : 2014-15
             State  Quarter 4  Quarter 1  Quarter 2  Quarter 3     Year
0          Florida  26082.622          0          0          0  2014-15
1       California  10002.983          0          0          0  2014-15
2         Virginia   7738.610          0          0          0  2014-15
3         Kentucky   5157.510          0          0          0  2014-15
4         New York   5005.106          0          0          0  2014-15
5            Texas   3114.332          0          0          0  2014-15
6       Washington   2757.892          0          0          0  2014-15
7         Arkansas   1859.400          0          0          0  2014-15
8         Illinois   1683.134          0          0          0  2014-15
9        Louisiana   1287.260          0          0          0  2014-15
10            Iowa   1190.840          0          0          0  2014-15
11        Michigan    971.496          0          0          0  2014-15
12  South Carolina    900.840          0      



 Year : 2017-18
                   State  Quarter 1   Quarter 2   Quarter 3   Quarter 4   
0             California  27691.481  30412.7905  46618.9920  22979.3730  \
1               New York  17818.292  17659.1400  24361.9080   5339.6720   
2           Pennsylvania  12888.306   9214.2270   7092.5730   6219.4890   
3             New Jersey  11211.076    868.4900   4716.2900    178.2100   
4               Illinois   7931.473   6003.1200   2139.1920   5683.6350   
5                  Texas   7897.892  14787.9962  10083.8348  12560.4272   
6               Virginia   6414.860   4750.9400   6190.3300   1291.7800   
7               Michigan   5412.690   5015.7300  16637.0310  11551.2150   
8                   Ohio   4329.421   4923.2320  13563.7320   3068.8110   
9                 Nevada   4088.008     86.2000   4848.4840      0.0000   
10               Georgia   3158.180   1566.5100   3528.1400   8081.0900   
11              Colorado   3038.323   4754.9220   2641.2180   1679.6160   
12     

In [218]:
# State contain name of all states in data
states=st['State'].unique()
states

array(['Kentucky', 'California', 'Florida', 'North Carolina',
       'Washington', 'Texas', 'Wisconsin', 'Utah', 'Nebraska',
       'Pennsylvania', 'Illinois', 'Minnesota', 'Michigan', 'Delaware',
       'Indiana', 'New York', 'Arizona', 'Virginia', 'Tennessee',
       'Alabama', 'South Carolina', 'Oregon', 'Colorado', 'Iowa', 'Ohio',
       'Missouri', 'Oklahoma', 'New Mexico', 'Louisiana', 'Connecticut',
       'New Jersey', 'Massachusetts', 'Georgia', 'Nevada', 'Rhode Island',
       'Mississippi', 'Arkansas', 'Montana', 'New Hampshire', 'Maryland',
       'District of Columbia', 'Kansas', 'Vermont', 'Maine',
       'South Dakota', 'Idaho', 'North Dakota', 'Wyoming',
       'West Virginia'], dtype=object)

In [219]:
i=0
fig_num=main_fig_num
title=f"Revenue Per State Of Each Quarter For Each Year"
fig_dict={}
for y in start_years:
    sub_title=f"Revenue Per State of Each Quarter in {years[i]}"
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    temp='st_'+str(y)+'_q_mix'
    for f in full_quarters:
        exec(f"{temp_fig}.add_trace(go.Bar(x=eval(temp)['State'],y=eval(temp)[f],name=f))")
    exec(f"{temp_fig}.update_layout(title=sub_title,title_font_size=24)")
    eval(temp_fig).show()
    # For data Transfer
    fig_dict[f"Year:{y}"]=[eval(temp_fig),eval(temp)]
    i=i+1
state_dict[title]=fig_dict

In [220]:
main_fig_num=fig_num
print(main_fig_num)

12


In [221]:
title=f"Revenue Per Year Of Each Quarter For Each State"
fig_num=main_fig_num
fig_dict={}
for st in states:
    temp = pd.DataFrame()
    for y in start_years:
        main_data='st_'+str(y)+'_q_mix'
        if temp.empty:
            temp=eval(main_data).loc[eval(main_data)['State']==st]
        else:
            temp = pd.concat([temp, eval(main_data).loc[eval(main_data)['State']==st]], ignore_index=True)
    if temp.empty==False:
        temp_fig='fig_'+str(fig_num)
        fig_num=fig_num+1;
        exec(f"{temp_fig}=go.Figure()")
        for f in full_quarters:
            exec(f"{temp_fig}.add_trace(go.Bar(x=temp['Year'],y=temp[f],name=f))")
        exec(f"{temp_fig}.update_layout(title='Revenue of {st} per Quarter in Each Year',title_font_size=24)")
        eval(temp_fig).show()
        fig_dict[f"State:{st}"]=[eval(temp_fig),temp]
state_dict[title]=fig_dict
print(fig_dict)


{'State:Kentucky': [Figure({
    'data': [{'name': 'Quarter 1',
              'type': 'bar',
              'x': array(['2014-15', '2015-16', '2016-17', '2017-18', '2018-19'], dtype=object),
              'y': array([   0.  , 2029.04,  987.58,   79.14, 1573.1 ])},
             {'name': 'Quarter 2',
              'type': 'bar',
              'x': array(['2014-15', '2015-16', '2016-17', '2017-18', '2018-19'], dtype=object),
              'y': array([   0.  ,   25.5 , 4723.04,  445.83, 2002.67])},
             {'name': 'Quarter 3',
              'type': 'bar',
              'x': array(['2014-15', '2015-16', '2016-17', '2017-18', '2018-19'], dtype=object),
              'y': array([    0.  ,   953.05,  1598.87,  3387.64, 11135.34])},
             {'name': 'Quarter 4',
              'type': 'bar',
              'x': array(['2014-15', '2015-16', '2016-17', '2017-18', '2018-19'], dtype=object),
              'y': array([5157.51,  364.07, 1190.28,  805.73,    0.  ])}],
    'layout': {'template'

In [222]:
main_fig_num=fig_num
print(main_fig_num)

61


In [223]:
main_data_dict['State Analysis']=state_dict

In [224]:
# Segment Analysis
if cdict['BasePrice'] and cdict['Segment'] and cdict['BillDate']:
    print(1)

1


In [225]:
# Making another copy of Data for doing Segment analysis
seg=df.copy() 
for y in start_years:
    temp='seg_'+str(y)
    temp2='df_'+str(y)
    exec(f"{temp}={temp2}.copy()")

In [226]:
# Dropping all the Column where SEGMENT in null
seg.dropna(subset=['Segment'], inplace=True)
for y in start_years:
    temp='seg_'+str(y)
    exec(f"{temp}.dropna(subset=['Segment'], inplace=True)")

In [227]:
# Segment contain name of all Segment in data
segments=seg['Segment'].unique()
segments

array(['Consumer', 'Corporate', 'Home Office'], dtype=object)

In [228]:
# Overall Revenue of each Segment
title="(Bar) Revenue Per Segment"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
segment_sale_all=seg.groupby("Segment").BasePrice.sum().sort_values(ascending = False).to_frame(name=f'BasePrice').reset_index()
exec(f"{temp_fig}=px.bar(segment_sale_all,x='Segment',y='BasePrice')")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
eval(temp_fig).show()
fig_dict={}
fig_dict["Total"]=[eval(temp_fig),segment_sale_all]
segment_dict[title]=fig_dict

# Pie Plot
title="(Pie) Revenue Per Segment"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
exec(f"{temp_fig} = px.pie(segment_sale_all, values='BasePrice', names='Segment')")
exec(f"{temp_fig}.update_layout(title='Overall Revenue Per Segment',title_font_size=24)")
eval(temp_fig).show()

# Data Transfer
fig_dict={}
fig_dict["Total"]=[eval(temp_fig),segment_sale_all]
segment_dict[title]=fig_dict

In [229]:
main_fig_num=fig_num
print(main_fig_num)

62


In [230]:
main_fig_num=fig_num
print(main_fig_num)

62


In [231]:
# Segment_Sale17 contain reveue of each state for year 2017-18
# Creating ya_Mix dataframe containg revenue per month for each year
segment_sale_mix=pd.DataFrame()
ind=0
for y in start_years:
    temp='seg_'+str(y)
    temp=eval(temp).groupby('Segment').BasePrice.sum().sort_values(ascending = False).to_frame(name=f'BasePrice{short_years[ind]}').reset_index()
    ind=ind+1
    if segment_sale_mix.empty:
        segment_sale_mix=temp
    else:
        segment_sale_mix= pd.merge(segment_sale_mix,temp, on='Segment',how='outer').fillna(0)


segment_sale_mix

Segment  BasePrice14-15  BasePrice15-16  BasePrice16-17   
0  Home Office       38160.238      56101.7318      89230.8882  \
1     Consumer       21933.787     281985.9052     271065.2687   
2    Corporate       13837.371     130194.8621     129468.5265   

   BasePrice17-18  BasePrice18-19  
0     106274.0414     135215.2775  
1     307797.2022     265278.3679  
2     215695.8256     199297.4896

In [232]:
title="(Bar) Revenue Per Segment of Each Year"
fig_dict={}
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
for y in short_years:
    temp='BasePrice'+str(y)
    exec(f"{temp_fig}.add_trace(go.Bar(x=segment_sale_mix['Segment'],y=segment_sale_mix[temp],name=temp))")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24,xaxis=dict(tickangle=315))")
eval(temp_fig).show()

# Data Transfer
fig_dict["All Year"]=[eval(temp_fig),segment_sale_mix]
segment_dict[title]=fig_dict


# Pie plot for Every year
title="(Pie) Revenue Per Segment of Each Year"
fig_dict={}
fig_num=main_fig_num
size=len(start_years)
ind=0
for y in start_years:
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.pie(segment_sale_mix, values=f'BasePrice{short_years[ind]}', names='Segment')")
    exec(f"{temp_fig}.update_layout(title=f'Revenue Per Segment in {years[ind]}',title_font_size=24)")
    eval(temp_fig).show();
    ind=ind+1;
    fig_dict[f"Year:{y}"]=[eval(temp_fig),segment_sale_mix]

# Data Transfer
segment_dict[title]=fig_dict

In [233]:
main_fig_num=fig_num
print(main_fig_num)

67


In [234]:
seg_all_quarter=df.groupby(['Segment','Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name='PriceAll').reset_index()
seg_all_q_mix=pd.DataFrame()
for q in quarters:
    temp=pd.DataFrame()
    temp=seg_all_quarter.loc[seg_all_quarter['Quarter'] == int(q)][['Segment','PriceAll']]
    temp.rename(columns = {'PriceAll':f'Quarter {q}'}, inplace = True)
    if seg_all_q_mix.empty:
        seg_all_q_mix=temp
    else:
        seg_all_q_mix= pd.merge(seg_all_q_mix,temp, on='Segment',how='outer').fillna(0)
        
seg_all_q_mix


Segment    Quarter 1    Quarter 2    Quarter 3    Quarter 4
0     Consumer  223092.6382  342126.3849  409946.8583  172894.6496
1    Corporate  131039.5389  175295.3990  289313.1907   92845.9462
2  Home Office   82075.0705   85533.2438  171878.1262   85495.7364

In [235]:
title="(Bar) Revenue Per Segment Of Each Quarter"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
for q in full_quarters:
    exec(f"{temp_fig}.add_trace(go.Bar(x=seg_all_q_mix['Segment'],y=seg_all_q_mix[q],name=q))")
exec(f"{temp_fig}.update_layout(title=f'Overall Revenue Per Segment for each Quarter',title_font_size=24,xaxis=dict(tickangle=315))")
eval(temp_fig).show()

# Data Transfer
fig_dict={}
fig_dict["Quarter"]=[eval(temp_fig),seg_all_q_mix]
segment_dict[title]=fig_dict

In [236]:
main_fig_num=fig_num
print(main_fig_num)

68


In [237]:
ind=0
for year in start_years:
    fetch_data='df_'+str(year)
    work_data='seg_'+str(year)+'_quarter'
    exec(f"{work_data}={fetch_data}.groupby(['Segment','Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name=f'Price{short_years[ind]}').reset_index()")
    main_data='seg_'+str(year)+'_q_mix'
    exec(f"{main_data}=pd.DataFrame()")
    
    for q in quarters:
        temp=pd.DataFrame()
        temp=eval(work_data).loc[eval(work_data)['Quarter'] == int(q)][['Segment',f'Price{short_years[ind]}']]
        temp.rename(columns = {f'Price{short_years[ind]}':f'Quarter {q}'}, inplace = True)
        if eval(main_data).empty:
            exec(f"{main_data}=temp")
        else:
            exec(f"{main_data}= pd.merge({main_data},temp, on='Segment',how='outer').fillna(0)")
    for q in full_quarters:
        if q not in eval(main_data).columns:
            exec(f"{main_data}[q] = 0.0")
    exec(f"{main_data}['Year']='{years[ind]}'")
    print(f"\n\n Year : {years[ind]}")
    ind=ind+1
    print(eval(main_data).to_string())



 Year : 2014-15
       Segment  Quarter 4  Quarter 1  Quarter 2  Quarter 3     Year
0  Home Office  38160.238        0.0        0.0        0.0  2014-15
1     Consumer  21933.787        0.0        0.0        0.0  2014-15
2    Corporate  13837.371        0.0        0.0        0.0  2014-15


 Year : 2015-16
       Segment   Quarter 1   Quarter 2   Quarter 3   Quarter 4     Year
0     Consumer  47575.3466  94993.0475  98454.6195  40962.8916  2015-16
1    Corporate  26856.1530  32992.5070  54111.4647  16234.7374  2015-16
2  Home Office  11442.5940  14537.0518  24962.0280   5160.0580  2015-16


 Year : 2016-17
       Segment   Quarter 1   Quarter 2   Quarter 3  Quarter 4     Year
0     Consumer  56242.9885  79035.9050  89114.5082  46671.867  2016-17
1    Corporate  18042.4645  33915.6682  51482.7288  26027.665  2016-17
2  Home Office  13427.9200  15608.6340  40207.5012  19986.833  2016-17


 Year : 2017-18
       Segment  Quarter 1   Quarter 2    Quarter 3   Quarter 4     Year
0     Consum

In [238]:
title="(Bar) Revenue Per Segment Of Each Quarter Per Year"
fig_dict={}
fig_num=main_fig_num
i=0
for y in start_years:
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    temp='seg_'+str(y)+'_q_mix'
    for q in full_quarters:
        exec(f"{temp_fig}.add_trace(go.Bar(x=eval(temp)['Segment'],y=eval(temp)[q],name=q))")
    exec(f"{temp_fig}.update_layout(title='Revenue Per Quarter of each Segment in {years[i]}',title_font_size=24,xaxis=dict(tickangle=315))")
    eval(temp_fig).show()
    fig_dict[f"Year:{y}"]=[eval(temp_fig),eval(temp)]
    i=i+1

# Data Transfer
segment_dict[title]=fig_dict

In [239]:
main_fig_num=fig_num
print(main_fig_num)

73


In [240]:
title="(Bar) Revenue Per Year Of Each Quarter For Each Segment"
fig_dict={}
fig_num=main_fig_num
for segment in segments:
    
    temp = pd.DataFrame()
    for segment in segments:
        for y in start_years:
            main_data='seg_'+str(y)+'_q_mix'
            if temp.empty:
                temp=eval(main_data).loc[eval(main_data)['Segment']==segment]
            else:
                temp=pd.concat([temp, eval(main_data).loc[eval(main_data)['Segment']==segment]], ignore_index=True)
    if temp.empty==False:
        temp_fig='fig_'+str(fig_num)
        fig_num=fig_num+1;
        exec(f"{temp_fig}=go.Figure()")
        for q in full_quarters:
            exec(f"{temp_fig}.add_trace(go.Bar(x=temp['Year'],y=temp[q],name=q))")
        exec(f"{temp_fig}.update_layout(title=f'Revenue of {segment} per Quarter in Each Year',title_font_size=24,xaxis=dict(tickangle=0))")
        eval(temp_fig).show()
        fig_dict[f"Segment:{segment}"]=[eval(temp_fig),temp]
    else:
        print(f"\nSegment is:{segment}")
        print(temp.to_string())
        

# Data Transfer
segment_dict[title]=fig_dict

In [241]:
main_fig_num=fig_num
print(main_fig_num)

76


In [242]:
seg_17_q_mix

Segment  Quarter 1   Quarter 2    Quarter 3   Quarter 4     Year
0     Consumer  69519.462  74439.3644  100512.2718  63326.1040  2017-18
1    Corporate  42016.220  42974.0218   93959.4110  36746.1728  2017-18
2  Home Office  23525.479  20642.9880   39916.9670  22188.6074  2017-18

In [243]:
title="(Pie) Revenue Per Segment Of Each Quarter For Each Year"
fig_dict={}
fig_num=main_fig_num
size=len(quarters)*len(start_years)
ind=0
ind2=0
for y in start_years:
    main_data='seg_'+str(y)+'_q_mix'
    for q in quarters:
        
        if (eval(main_data)[f'Quarter {q}'] == 0).all():
            print(f"\n\nData For Quarter {q} of {years[ind]} is Not Present\n\n")
        else:
            temp_fig='fig_'+str(fig_num)
            fig_num=fig_num+1;
            exec(f"{temp_fig}=go.Figure()")
            exec(f"new_data={main_data}[['Segment','Quarter {q}']].copy()")
            exec(f"{temp_fig} = px.pie(new_data, values=f'Quarter {q}', names='Segment')")
            exec(f"{temp_fig}.update_layout(title='Revenue of Year : {years[ind]} , Quarter {q}',title_font_size=24)")
            eval(temp_fig).show()
            fig_dict[f"Year:{y}, Quarter:{q}"]=[eval(temp_fig),new_data]
        ind2=ind2+1;
    ind=ind+1

# Data Transfer
segment_dict[title]=fig_dict



Data For Quarter 1 of 2014-15 is Not Present




Data For Quarter 2 of 2014-15 is Not Present




Data For Quarter 3 of 2014-15 is Not Present






Data For Quarter 4 of 2018-19 is Not Present




In [244]:
main_fig_num=fig_num
print(main_fig_num)

92


In [245]:
main_data_dict["Segment Analysis"]=segment_dict

In [246]:
# Function for doing all analysis for differnt columns
def col_analysis(val,col_val,x,rotate,main_fig_num):
    product_dict={}
    figures = {}
    fig_num=main_fig_num
#   Creating data copy in pl1_17 format
    pl=new_data.copy()
    pl.dropna(subset=[val], inplace=True)
    for y in start_years:
        temp='pl_'+str(y)
        temp2='new_data_'+str(y)
        exec(f"{temp}={temp2}.copy()")
        exec(f"{temp}.dropna(subset=[val], inplace=True)")
        
#   Finding all the unique values in Product Level  
    pl_values=pl[val].unique()
    
#   Plotting Overall Revenue per Product of Product Level
    global temp_fig
    title=f"(Bar) Revenue Per Value of {val}"
    temp_fig='fig_'+str(fig_num)
    exec(f"global {temp_fig};{temp_fig}=go.Figure()")
    pl_sale_all=pl.groupby(val).BasePrice.sum().sort_values(ascending = False).to_frame(name=f'BasePrice').reset_index()
    exec(f"{temp_fig}=px.bar(pl_sale_all,x=val,y='BasePrice')")
    exec(f"{temp_fig}.update_layout(title=title,title_font_size=24,xaxis=dict(tickangle=rotate))")
    eval(temp_fig).show()
    figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
    fig_num=fig_num+1;
    fig_dict={}
    fig_dict["Total"]=[eval(temp_fig),pl_sale_all]
    product_dict[title]=fig_dict
    
    
#     Pie Plot of Revenue per Product in Product Level
    title=f"(Pie) Revenue Per Value of {val}"
    temp_fig='fig_'+str(fig_num)
    exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.pie(pl_sale_all, values='BasePrice', names=val)")
    exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
    eval(temp_fig).show()
    figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
    fig_num=fig_num+1;
    fig_dict={}
    fig_dict["Total"]=[eval(temp_fig),pl_sale_all]
    product_dict[title]=fig_dict
    
#   Finding the revenue of each product in our product level for each year 
    pl_sale_mix=pd.DataFrame()
    ind=0
    for y in start_years:
        temp='pl_'+str(y)
        temp=eval(temp).groupby(val).BasePrice.sum().sort_values(ascending = False).to_frame(name=f'BasePrice{short_years[ind]}').reset_index()
        ind=ind+1
        if pl_sale_mix.empty:
            pl_sale_mix=temp
        else:
            pl_sale_mix= pd.merge(pl_sale_mix,temp, on=val,how='outer').fillna(0)
            
#   Plotting Revenue of each product in product level each year
    title=f"(Bar) Revenue Per Value in {val} of Each Year"
    temp_fig='fig_'+str(fig_num)
    exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
    for y in short_years:
        temp='BasePrice'+str(y)
        exec(f"{temp_fig}.add_trace(go.Bar(x=pl_sale_mix[val],y=pl_sale_mix[temp],name=temp))")
    exec(f"{temp_fig}.update_layout(title='Revenue Per Product in {col_val} in Each Year',title_font_size=24,xaxis=dict(tickangle=rotate))")
    eval(temp_fig).show()
    figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
    fig_num=fig_num+1;
    
    # Data Transfer
    fig_dict={}
    fig_dict["All Year"]=[eval(temp_fig),pl_sale_mix]
    product_dict[title]=fig_dict

# Pie Chart of Revenue per year of each product in product level 
    title=f"(Pie) Revenue Per Value in {val} of Each Year"
    fig_dict={}
    size=len(start_years)
    ind=0
    for y in start_years:
        temp_fig='fig_'+str(fig_num)
        exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
        exec(f"{temp_fig} = px.pie(pl_sale_mix, values=f'BasePrice{short_years[ind]}', names=val)")
        exec(f"{temp_fig}.update_layout(title='Revenue Per Product in {col_val} in {years[ind]}',title_font_size=24)")
        eval(temp_fig).show();
        figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
        fig_num=fig_num+1;
        ind=ind+1;
        fig_dict[f"Year:{y}"]=[eval(temp_fig),pl_sale_mix]
    product_dict[title]=fig_dict

# Making dataframe with product level and its revenue in each quarter
    pl_all_quarter=pl.groupby([val,'Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name='PriceAll').reset_index()
    pl_all_q_mix=pd.DataFrame()
    for q in quarters:
        temp=pd.DataFrame()
        temp=pl_all_quarter.loc[pl_all_quarter['Quarter'] == int(q)][[val,'PriceAll']]
        temp.rename(columns = {'PriceAll':f'Quarter {q}'}, inplace = True)
        if pl_all_q_mix.empty:
            pl_all_q_mix=temp
        else:
            pl_all_q_mix= pd.merge(pl_all_q_mix,temp, on=val,how='outer').fillna(0)

#    Plotting revenue per product of product level in each quarter
    title=f"(Bar) Revenue Per Value in {val} of Each Quarter"
    temp_fig='fig_'+str(fig_num)
    exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
    for q in full_quarters:
        exec(f"{temp_fig}.add_trace(go.Bar(x=pl_all_q_mix[val],y=pl_all_q_mix[q],name=q))")
    exec(f"{temp_fig}.update_layout(title=title,title_font_size=24,xaxis=dict(tickangle=rotate))")
    eval(temp_fig).show()
    figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
    fig_num=fig_num+1;
    # Data Transfer
    fig_dict={}
    fig_dict["Quarter"]=[eval(temp_fig),pl_all_q_mix]
    product_dict[title]=fig_dict

#   Finding Revenue of each product level value per quarter for each year seperately 
    ind=0
    title=f"(Bar) Revenue Per Value in {val} of Each Quarter Per Year"
    fig_dict={}
    for year in start_years:
        fetch_data='new_data_'+str(year)
        work_data='pl_'+str(year)+'_quarter'
        exec(f"{work_data}={fetch_data}.groupby([val,'Quarter']).BasePrice.sum().sort_values(ascending = False).to_frame(name=f'Price{short_years[ind]}').reset_index()")
        main_data='pl_'+str(year)+'_q_mix'
        exec(f"{main_data}=pd.DataFrame()")
        for q in quarters:
            temp=pd.DataFrame()
            temp=eval(work_data).loc[eval(work_data)['Quarter'] == int(q)][[val,f'Price{short_years[ind]}']]
            temp.rename(columns = {f'Price{short_years[ind]}':f'Quarter {q}'}, inplace = True)
            if eval(main_data).empty:
                exec(f"{main_data}=temp")
            else:
                exec(f"{main_data}= pd.merge({main_data},temp, on=val,how='outer').fillna(0)")
        for q in full_quarters:
            if q not in eval(main_data).columns:
                exec(f"{main_data}[q] = 0.0")
        exec(f"{main_data}['Year']='{years[ind]}'")
        
#   Plotting Revenue Per Quarter of each Product Level Value for each year seperately
        
        temp_fig='fig_'+str(fig_num)
        exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
        for q in full_quarters:
            exec(f"{temp_fig}.add_trace(go.Bar(x=eval(main_data)[val],y=eval(main_data)[q],name=q))")
        exec(f"{temp_fig}.update_layout(title='Revenue Per Quarter of each Product Type in {years[ind]}',title_font_size=24,xaxis=dict(tickangle=rotate))")
        eval(temp_fig).show()
        figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
        fig_num=fig_num+1;
        ind=ind+1;
        globals()[main_data] = locals()[main_data]
        fig_dict[f"Year:{year}"]=[eval(temp_fig),eval(main_data)]
    # Data Transfer
    product_dict[title]=fig_dict
            
        
#   Plotting Quartey and yearly analysis of each product seperately
    title=f"(Bar) Revenue Per Year Of Each Quarter For Each value of {val}"
    fig_dict={}
    for product in pl_values:
        temp = pd.DataFrame()
        for y in start_years:
            main_data='pl_'+str(y)+'_q_mix'
            if temp.empty:
                temp=eval(main_data).loc[eval(main_data)[val]==product]
            else:
                temp=pd.concat([temp, eval(main_data).loc[eval(main_data)[val]==product]], ignore_index=True)
        if temp.empty==False:
            temp_fig='fig_'+str(fig_num)
            exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
            for q in full_quarters:
                exec(f"{temp_fig}.add_trace(go.Bar(x=temp['Year'],y=temp[q],name=q))")
            exec(f"{temp_fig}.update_layout(title='Revenue of {product} per Quarter in Each Year',title_font_size=24,xaxis=dict(tickangle=rotate))")
            eval(temp_fig).show()
            figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
            fig_num=fig_num+1;
            fig_dict[f"{col_val}:{product}"]=[eval(temp_fig),temp]
    product_dict[title]=fig_dict       
            
# Pie char of revenue of every quarter for every year
    title=f"(Pie) Revenue Per Value in {val} Of Each Quarter For Each Year"
    fig_dict={}
    size=len(quarters)*len(start_years)
    ind=0
    ind2=0
    for y in start_years:
        main_data='pl_'+str(y)+'_q_mix'
        for q in quarters:
            if (eval(main_data)[f'Quarter {q}'] == 0).all():
                print(f"\n\nData For Quarter {q} of {years[ind]} is Not Present\n\n")
            else:
                temp_fig='fig_'+str(fig_num)
                exec(f"global {temp_fig}; {temp_fig}=go.Figure()")
                exec(f"{temp_fig} = px.pie(eval(main_data), values=f'Quarter {q}', names=val)")
                exec(f"{temp_fig}.update_layout(title='Revenue of Year : {years[ind]} , Quarter {q}',title_font_size=24)")
                eval(temp_fig).show()
                figures[f"{temp_fig}_{fig_num}"] = eval(temp_fig)
                fig_num=fig_num+1;
                fig_dict[f"Year:{y}, Quarter:{q}"]=[eval(temp_fig),eval(main_data)]
            ind2=ind2+1;
        ind=ind+1
    product_dict[title]=fig_dict
    main_data_dict[f"{col_val} Analysis"]=product_dict
    return fig_num,figures

In [247]:
#Product Level 1 Analysis
if cdict['BasePrice'] and cdict['PL'] and cdict['BillDate']:
    print(1)

1


In [248]:
# Creating this to assign images after running function 
prev_main_fig_num=main_fig_num

In [249]:
# 1sr Aurgument = Database to work on
# 2st Aurgument = Column Name to be analyzed
# 3nd Aurgument = Complete Column Name in full form 
# 4rd Aurgument = Number of Last few product for which we need more description
# 5th Aurgument = Degree of Ratation of x axis value
# 6th Aurgument is auto aurguement for refrencing figure number

In [250]:
new_data=df.copy()
# Creating multiple dataframe from our new dataframe of updated columns for each year
for y in start_years:
    temp='new_data_'+str(y)
    x=int(y)+1
    exec(f"{temp}=new_data.loc[(new_data['BillDate'] >= '20{y}-04-01') & (new_data['BillDate'] <= '20{x}-03-31')]")

In [251]:
fig_num,figures=col_analysis('PL1','Product Level 1',0,315,main_fig_num)



Data For Quarter 1 of 2014-15 is Not Present




Data For Quarter 2 of 2014-15 is Not Present




Data For Quarter 3 of 2014-15 is Not Present






Data For Quarter 4 of 2018-19 is Not Present




In [252]:
for key, value in figures.items():
    temp='fig_'+str(prev_main_fig_num)
    exec(f"{temp}=figures[key]")
    prev_main_fig_num=prev_main_fig_num+1

In [253]:
main_fig_num=fig_num

In [254]:
# If we want analysis of some other column like segment and state then we should follow the below template

In [255]:
# Extra Analysis Start

In [256]:
# Creating a variable for containig image number

prev_main_fig_num=main_fig_num

# Copying df to data for doing some changes in our data

new_data=df.copy()


# Provide the name of column in temp for which you want to perform analysis
temp='State' 
val=new_data[temp].unique()
print(val)

['Kentucky' 'California' 'Florida' 'North Carolina' 'Washington' 'Texas'
 'Wisconsin' 'Utah' 'Nebraska' 'Pennsylvania' 'Illinois' 'Minnesota'
 'Michigan' 'Delaware' 'Indiana' 'New York' 'Arizona' 'Virginia'
 'Tennessee' 'Alabama' 'South Carolina' 'Oregon' 'Colorado' 'Iowa' 'Ohio'
 'Missouri' 'Oklahoma' 'New Mexico' 'Louisiana' 'Connecticut' 'New Jersey'
 'Massachusetts' 'Georgia' 'Nevada' 'Rhode Island' 'Mississippi'
 'Arkansas' 'Montana' 'New Hampshire' 'Maryland' 'District of Columbia'
 'Kansas' 'Vermont' 'Maine' 'South Dakota' 'Idaho' 'North Dakota'
 'Wyoming' 'West Virginia']


In [257]:
# We need to edit the data here according to our data as if there are 50 differnt value in column we are providing then the pie chart will not be represented as expected
# Provide the name of different state for which you want to see the analysis

new_data=new_data[new_data[temp].isin(['Kentucky','Idaho','Florida'])]


In [258]:
val=new_data[temp].unique()
print(val)

['Kentucky' 'Florida' 'Idaho']


In [259]:
# Creating multiple dataframe from our new dataframe of updated columns for each year
for y in start_years:
    new_temp='new_data_'+str(y)
    x=int(y)+1
    exec(f"{new_temp}=new_data.loc[(new_data['BillDate'] >= '20{y}-04-01') & (new_data['BillDate'] <= '20{x}-03-31')]")

In [260]:
# 1sr Aurgument = Database to work on
# 2st Aurgument = Column Name to be analyzed (Name this column different everytime you use as it should detect as diffent key for our dictionary)
# 3nd Aurgument = Complete Column Name in full form 
# 4rd Aurgument = Number of Last few product for which we need more description
# 5th Aurgument = Degree of Rotation of x axis value
# 6th Aurgument is auto aurguement for refrencing figure number

# Provide a detail name of column or the name of column to be shown in plots
temp2 = 'States'
fig_num,figures=col_analysis(temp,temp2,0,315,main_fig_num)



Data For Quarter 1 of 2014-15 is Not Present




Data For Quarter 2 of 2014-15 is Not Present




Data For Quarter 3 of 2014-15 is Not Present






Data For Quarter 4 of 2018-19 is Not Present




In [261]:
for key, value in figures.items():
    temp='fig_'+str(prev_main_fig_num)
    exec(f"{temp}=figures[key]")
    prev_main_fig_num=prev_main_fig_num+1
main_fig_num=fig_num

In [262]:
# Extra Analysis End

In [263]:
# Basic RFM Analysis
if cdict['BasePrice'] and cdict['CustomerName'] and cdict['BillDate']:
    print(1)

1


In [264]:
# Making Copy of Data to use while doing rfm analysis 
# rfm contain all the data, rfm_17 contain data of year 2017-18 and so on
rfm=df.copy() 
for y in start_years:
    temp='rfm_'+str(y)
    temp2='df_'+str(y)
    exec(f"{temp}={temp2}.copy()")

In [265]:
# List of All the Customers and total revenue generated by them
df.groupby("CustomerName").BasePrice.sum().sort_values(ascending = False)

CustomerName
Sean Miller        25043.050
Tamara Chand       19052.218
Raymond Buch       15117.339
Tom Ashbrook       14595.620
Adrian Barton      14473.571
                     ...    
Mitch Gastineau       16.739
Carl Jackson          16.520
Sung Chung            14.112
Lela Donovan           5.304
Thais Sissman          4.833
Name: BasePrice, Length: 793, dtype: float64

In [266]:
# RFM_Recency contain the Customer Name with the recency value


# Recency Means days passed after his last purchase
# Here we find the last purchse data of each customer
rfm_recency = rfm.groupby(by='CustomerName',as_index=False)['BillDate'].max()
rfm_recency.columns = ['CustomerName','LastPurchaseDate']

# Getting the most recent data means the end date of our data
recent_date = rfm_recency['LastPurchaseDate'].max()

# Finding recency column in days by substracting recent date by customer last purchase date
rfm_recency['Recency'] = rfm_recency['LastPurchaseDate'].apply(lambda x: (recent_date-x).days)
rfm_recency=rfm_recency.sort_values(by = 'Recency')
rfm_recency


# Frequency Means number of time a customer has made its purchase
rfm_frequency = rfm.drop_duplicates().groupby(by=['CustomerName'], as_index=False)['BillDate'].count()
rfm_frequency.columns = ['CustomerName', 'Frequency']
rfm_frequency=rfm_frequency.sort_values(by = 'Frequency',ascending=False)
rfm_frequency


# Monetary Mean the overall revenue generated by a customer in all the years
rfm_monetary = rfm.groupby(by='CustomerName', as_index=False)['BasePrice'].sum()
rfm_monetary.columns = ['CustomerName', 'Monetary']
rfm_monetary=rfm_monetary.sort_values(by = 'Monetary',ascending=False)
rfm_monetary


# RFM_MIX contain all recency frequency and monetary value of a customer
rfm_mix = rfm_recency.merge(rfm_frequency, on='CustomerName')
rfm_mix = rfm_mix.merge(rfm_monetary, on='CustomerName')
rfm_mix=rfm_mix.drop(columns='LastPurchaseDate')

print(rfm_mix.sort_values(by='Monetary',ascending=False))


        CustomerName  Recency  Frequency   Monetary
409      Sean Miller       79         15  25043.050
706     Tamara Chand      399         12  19052.218
447     Raymond Buch       96         18  15117.339
377     Tom Ashbrook       69         10  14595.620
266    Adrian Barton       41         20  14473.571
..               ...      ...        ...        ...
652  Mitch Gastineau      264          2     16.739
690     Carl Jackson      365          1     16.520
718       Sung Chung      414          1     14.112
754     Lela Donovan      552          1      5.304
687    Thais Sissman      357          2      4.833

[793 rows x 4 columns]


In [267]:
# The .rank function will give ranking to a customer according to its position among all the customer in a particular column
rfm_mix['R_rank'] = rfm_mix['Recency'].rank(ascending=False)
rfm_mix['F_rank'] = rfm_mix['Frequency'].rank(ascending=True)
rfm_mix['M_rank'] = rfm_mix['Monetary'].rank(ascending=True)

# Normalizing the rank into a value of 100 by dividing each rank by max possible rank and multiply by 100
rfm_mix['R_rank_norm'] = (rfm_mix['R_rank']/rfm_mix['R_rank'].max())*100
rfm_mix['F_rank_norm'] = (rfm_mix['F_rank']/rfm_mix['F_rank'].max())*100
rfm_mix['M_rank_norm'] = (rfm_mix['M_rank']/rfm_mix['M_rank'].max())*100


rfm_mix


CustomerName  Recency  Frequency   Monetary  R_rank  F_rank  M_rank   
0    Patrick O'Donnell        0         13  2493.2140   791.5   470.5   445.0  \
1          Chuck Clark        0         19  2870.0500   791.5   677.0   503.0   
2           Erica Bern        0          6  1643.2550   791.5   107.0   304.0   
3        Jill Matthias        0          7   303.9480   791.5   152.5    46.0   
4         Michael Chen        1         14  3805.7140   786.5   521.5   605.0   
..                 ...      ...        ...        ...     ...     ...     ...   
788   Valerie Takahito      999          9  1736.5960     5.0   255.5   323.0   
789     Craig Molinari     1034         13  3984.4524     4.0   470.5   620.0   
790    Ricardo Emerson     1097          1    48.3600     3.0     3.5     8.0   
791  Georgia Rosenberg     1135          5  1284.3800     2.0    72.5   236.0   
792     Nicole Brennan     1165          2   273.8720     1.0    12.0    42.0   

     R_rank_norm  F_rank_norm  M_rank_norm  
0     100.000000    59.331652    56.116015  
1     100.000000    85.372005    63.430013  
2     100.000000    13.493064    38.335435  
3     100.000000    19.230769     5.800757  
4      99.368288    65.762926    76.292560  
..           ...          ...          ...  
788     0.631712    32.219420    40.731400  
789     0.505370    59.331652    78.184111  
790     0.379027     0.441362     1.008827  
791     0.252685     9.142497    29.760404  
792     0.126342     1.513241     5.296343  

[793 rows x 10 columns]

In [268]:
# Finding overall rank = 0.15*Recency + 0.28*Frequency + 0.57*Monetary
# This value can be changed as required for considering differnt aspect of analysis
rfm_mix['RFM_Score'] = 0.15*rfm_mix['R_rank_norm']+0.28 * rfm_mix['F_rank_norm']+0.57*rfm_mix['M_rank_norm']
rfm_mix['RFM_Score'] *= 0.05
rfm_mix = rfm_mix.round(2)

# Removing Extra column and sorting the customer according to rfm score
rfm_mix_sorted=rfm_mix
rfm_mix_sorted = rfm_mix_sorted.sort_values(by='RFM_Score',ascending=False)
rfm_mix_sorted=rfm_mix_sorted[['CustomerName', 'RFM_Score']]
rfm_mix_sorted

CustomerName  RFM_Score
124         John Lee       4.81
64         Pete Kriz       4.79
227        Greg Tran       4.72
16       Harry Marie       4.71
63      Sanjit Engle       4.71
..               ...        ...
767   Phillip Breyer       0.12
749   Anemone Ratner       0.11
718       Sung Chung       0.09
754     Lela Donovan       0.05
790  Ricardo Emerson       0.04

[793 rows x 2 columns]

In [269]:
# We have RFM Score in Range 0-5 we seperate it in 5 segment with rfm range as:
# 1) Top Customer > 4.5
# 2) High Value Customer > 4
# 3) Medium Value Customer > 3
# 4)Low Value Customer > 1.6
# 5) High Value Customer > 0
# This value can also be altered as required
rfm_mix["Customer_segment"] = np.where(rfm_mix['RFM_Score'] >4.5, "Top Customer",(np.where(rfm_mix['RFM_Score'] > 4,"High Value Customer",(np.where(rfm_mix['RFM_Score'] > 3,"Medium Value Customer",(np.where(rfm_mix['RFM_Score'] > 1.6,"Low Value Customer","Lost Customer")))))))
rfm_mix[['CustomerName', 'RFM_Score', 'Customer_segment']]

CustomerName  RFM_Score       Customer_segment
0    Patrick O'Donnell       3.18  Medium Value Customer
1          Chuck Clark       3.75  Medium Value Customer
2           Erica Bern       2.03     Low Value Customer
3        Jill Matthias       1.18          Lost Customer
4         Michael Chen       3.84  Medium Value Customer
..                 ...        ...                    ...
788   Valerie Takahito       1.62     Low Value Customer
789     Craig Molinari       3.06  Medium Value Customer
790    Ricardo Emerson       0.04          Lost Customer
791  Georgia Rosenberg       0.98          Lost Customer
792     Nicole Brennan       0.17          Lost Customer

[793 rows x 3 columns]

In [270]:
title="(Pie) General RFM Analysis"
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
rfm_segment_counts = rfm_mix['Customer_segment'].value_counts()
exec(f"{temp_fig} = px.pie(rfm_mix, values=rfm_segment_counts.values,names=rfm_segment_counts.index)")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
for x,trace in enumerate(eval(temp_fig).data):
    trace.marker.colors = [color_map[l] for l in trace.labels]
eval(temp_fig).show()


fig_dict={}
fig_dict["Basic"]=[eval(temp_fig),rfm_mix[['CustomerName', 'RFM_Score', 'Customer_segment']]]
rfm_dict[title]=fig_dict

In [271]:
main_fig_num=fig_num
print(main_fig_num)

159


In [272]:
# Quantile-based discretization Method of RFM Analysis

In [273]:
# Copyting rfm_mix for doing quantitle analysis for rfm
rfm_q=rfm_mix[['CustomerName','R_rank','F_rank','M_rank']].copy()
rfm_q

CustomerName  R_rank  F_rank  M_rank
0    Patrick O'Donnell   791.5   470.5   445.0
1          Chuck Clark   791.5   677.0   503.0
2           Erica Bern   791.5   107.0   304.0
3        Jill Matthias   791.5   152.5    46.0
4         Michael Chen   786.5   521.5   605.0
..                 ...     ...     ...     ...
788   Valerie Takahito     5.0   255.5   323.0
789     Craig Molinari     4.0   470.5   620.0
790    Ricardo Emerson     3.0     3.5     8.0
791  Georgia Rosenberg     2.0    72.5   236.0
792     Nicole Brennan     1.0    12.0    42.0

[793 rows x 4 columns]

In [274]:
# Here we cut the Recency rank into 5 equal quantitle and labelled them
rfm_q['r'] = pd.qcut(rfm_q['R_rank'], q=5, labels=[5, 4, 3, 2, 1])

In [275]:
# Displaying the Customer count in each quantitle and the min and max recency  and avg recency
rfm_q.groupby('r').agg(
    count=('CustomerName', 'count'),
    min_recency=('R_rank', min),
    max_recency=('R_rank', max),
    avg_recency=('R_rank', 'mean')
).sort_values(by='avg_recency')

count  min_recency  max_recency  avg_recency
r                                              
5    159          1.0        158.5         80.0
4    159        160.5        317.5        239.0
3    158        319.5        471.5        397.5
2    164        477.5        636.5        558.5
1    153        644.5        791.5        717.0

In [276]:
# Doing the above analysis for Monetarty
rfm_q['m'] = pd.qcut(rfm_q['M_rank'], q=5, labels=[1, 2, 3, 4, 5])
rfm_q.groupby('m').agg(
    count=('CustomerName', 'count'),
    min_monetary=('M_rank', min),
    max_monetary=('M_rank', max),
    avg_monetary=('M_rank', 'mean')
).sort_values(by='avg_monetary')


count  min_monetary  max_monetary  avg_monetary
m                                                 
1    159           1.0         159.0          80.0
2    158         160.0         317.0         238.5
3    159         318.0         476.0         397.0
4    158         477.0         634.0         555.5
5    159         635.0         793.0         714.0

In [277]:
# Analysis for frequency
rfm_q['f'] = pd.qcut(rfm_q['F_rank'].rank(method='first'), q=5, labels=[1, 2, 3, 4, 5])
rfm_q.groupby('f').agg(
    count=('CustomerName', 'count'),
    min_frequency=('F_rank', min),
    max_frequency=('F_rank', max),
    avg_frequency=('F_rank', 'mean')
).sort_values(by='avg_frequency')


count  min_frequency  max_frequency  avg_frequency
f                                                    
1    159            3.5          152.5      81.971698
2    158          152.5          316.5     240.389241
3    159          316.5          470.5     394.849057
4    158          470.5          628.0     554.075949
5    159          628.0          793.0     713.716981

In [278]:
# Finding rfm score by adding all three value as a character
rfm_q['rfm'] = rfm_q['r'].astype(str) +\
               rfm_q['f'].astype(str) +\
               rfm_q['m'].astype(str)

In [279]:
# Fiding RFM Score by adding all three value as a integer
rfm_q['RFM_Score'] = rfm_q['r'].astype(int) +\
                     rfm_q['f'].astype(int) +\
                     rfm_q['m'].astype(int)
rfm_q.head()

CustomerName  R_rank  F_rank  M_rank  r  m  f  rfm  RFM_Score
0  Patrick O'Donnell   791.5   470.5   445.0  1  3  3  133          7
1        Chuck Clark   791.5   677.0   503.0  1  4  5  154         10
2         Erica Bern   791.5   107.0   304.0  1  2  1  112          4
3      Jill Matthias   791.5   152.5    46.0  1  1  1  111          3
4       Michael Chen   786.5   521.5   605.0  1  4  4  144          9

In [280]:
rfm_q.groupby('RFM_Score').agg(
    customers=('CustomerName', 'count'),
    mean_recency=('R_rank', 'mean'),
    mean_frequency=('F_rank', 'mean'),
    mean_monetary=('M_rank', 'mean'),
).sort_values(by='RFM_Score')

customers  mean_recency  mean_frequency  mean_monetary
RFM_Score                                                        
3                 12    713.458333       88.416667      66.416667
4                 29    644.913793      155.293103     112.586207
5                 38    535.210526      155.210526     150.394737
6                 47    447.723404      200.170213     181.978723
7                115    349.052174      212.982609     204.730435
8                107    385.859813      311.443925     324.168224
9                 95    424.478947      408.136842     421.610526
10               106    384.882075      472.754717     460.443396
11               100    435.025000      563.970000     569.080000
12                67    345.641791      602.358209     607.880597
13                45    259.577778      624.200000     646.844444
14                25    185.280000      688.080000     695.840000
15                 7     93.071429      743.142857     751.571429

In [281]:
# As the R,F,M value is in range 1,5 both inclusive the minimum rfm score value is 3 and maximum is 15
# We seperate this rfm score in 5 segment
# 1) Top Customer > 13
# 2) High Value Customer > 11
# 3) Medium Value Customer > 9
# 4)Low Value Customer > 6
# 5) High Value Customer > 0
# This value can also be altered as required

rfm_q["Customer_segment"] = np.where(rfm_q['RFM_Score']>=13, "Top Customer",(np.where(rfm_q['RFM_Score'] >= 11,"High Value Customer",(np.where(rfm_q['RFM_Score'] >=9,"Medium Value Customer",(np.where(rfm_q['RFM_Score'] >=6,"Low Value Customer",'Lost Customer')))))))
rfm_q[['CustomerName', 'RFM_Score', 'Customer_segment']]

CustomerName  RFM_Score       Customer_segment
0    Patrick O'Donnell          7     Low Value Customer
1          Chuck Clark         10  Medium Value Customer
2           Erica Bern          4          Lost Customer
3        Jill Matthias          3          Lost Customer
4         Michael Chen          9  Medium Value Customer
..                 ...        ...                    ...
788   Valerie Takahito         10  Medium Value Customer
789     Craig Molinari         13           Top Customer
790    Ricardo Emerson          7     Low Value Customer
791  Georgia Rosenberg          8     Low Value Customer
792     Nicole Brennan          7     Low Value Customer

[793 rows x 3 columns]

In [282]:
title='(Pie) Qunatile RFM Analysis'
fig_num=main_fig_num
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
rfm_segment_counts = rfm_q['Customer_segment'].value_counts()
exec(f"{temp_fig} = px.pie(rfm_q, values=rfm_segment_counts.values, names=rfm_segment_counts.index)")
exec(f"{temp_fig}.update_layout(title=title,title_font_size=24)")
for x,trace in enumerate(eval(temp_fig).data):
    trace.marker.colors = [color_map[l] for l in trace.labels]
eval(temp_fig).show()

# For data Transfer to dictionary for Dashboard
fig_dict={}
fig_dict["Quantile"]=[eval(temp_fig),rfm_q[['CustomerName', 'RFM_Score', 'Customer_segment']]]
rfm_dict[title]=fig_dict


In [283]:
main_fig_num=fig_num
print(main_fig_num)

160


In [284]:
# This is RFM Analysis using Quantile method for every year seperately
title='(Pie) Quantitle RFM Analysis Of Each Year'
fig_dict={}
ind=0
fig_num=main_fig_num
for y in start_years:
    final_data='rfm_q_'+str(y)
    temp2='df_'+str(y)
    exec(f"rfm_y={temp2}.copy()")
    rfm_y_recency = rfm_y.groupby(by='CustomerName',as_index=False)['BillDate'].max()
    rfm_y_recency.columns = ['CustomerName','LastPurchaseDate']
    recent_date = rfm_y_recency['LastPurchaseDate'].max()
    rfm_y_recency['Recency'] = rfm_y_recency['LastPurchaseDate'].apply(lambda x: (recent_date-x).days)
    rfm_y_recency=rfm_y_recency.sort_values(by = 'Recency')
    rfm_y_frequency = rfm_y.drop_duplicates().groupby(by=['CustomerName'], as_index=False)['BillDate'].count()
    rfm_y_frequency.columns = ['CustomerName', 'Frequency']
    rfm_y_frequency=rfm_y_frequency.sort_values(by = 'Frequency',ascending=False)
    rfm_y_monetary = rfm_y.groupby(by='CustomerName', as_index=False)['BasePrice'].sum()
    rfm_y_monetary.columns = ['CustomerName', 'Monetary']
    rfm_y_monetary=rfm_y_monetary.sort_values(by = 'Monetary',ascending=False)
    rfm_y_mix = rfm_y_recency.merge(rfm_y_frequency, on='CustomerName')
    rfm_y_mix = rfm_y_mix.merge(rfm_y_monetary, on='CustomerName')
    rfm_y_mix = rfm_y_mix.drop(columns='LastPurchaseDate')
    
    rfm_y_mix['R_rank'] = rfm_y_mix['Recency'].rank(ascending=False)
    rfm_y_mix['F_rank'] = rfm_y_mix['Frequency'].rank(ascending=True)
    rfm_y_mix['M_rank'] = rfm_y_mix['Monetary'].rank(ascending=True)
    rfm_q_y=rfm_y_mix[['CustomerName','R_rank','F_rank','M_rank']].copy()
    rfm_q_y['r'] = pd.qcut(rfm_q_y['R_rank'], q=5, labels=[5, 4, 3, 2, 1])
    rfm_q_y['m'] = pd.qcut(rfm_q_y['M_rank'], q=5, labels=[1, 2, 3, 4, 5])
    rfm_q_y['f'] = pd.qcut(rfm_q_y['F_rank'].rank(method='first'), q=5, labels=[1, 2, 3, 4, 5])
    rfm_q_y['rfm'] = rfm_q_y['r'].astype(str) +\
                     rfm_q_y['f'].astype(str) +\
                     rfm_q_y['m'].astype(str)
    rfm_q_y['RFM_Score'] = rfm_q_y['r'].astype(int) +\
                           rfm_q_y['f'].astype(int) +\
                           rfm_q_y['m'].astype(int)

    rfm_q_y["Customer_segment"] = np.where(rfm_q_y['RFM_Score']>=13, "Top Customer",(np.where(rfm_q_y['RFM_Score'] >= 11,"High Value Customer",(np.where(rfm_q_y['RFM_Score'] >=9,"Medium Value Customer",(np.where(rfm_q_y['RFM_Score'] >=6,"Low Value Customer",'Lost Customer')))))))
    rfm_q_y[['CustomerName', 'RFM_Score', 'Customer_segment']]
    rfm_segment_counts = rfm_q_y['Customer_segment'].value_counts()
    
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.pie(rfm_q_y, values=rfm_segment_counts.values, names=rfm_segment_counts.index)")
    exec(f"{temp_fig}.update_layout(title='Qunatile RFM Analysis of {years[ind]}',title_font_size=24)")
    for x,trace in enumerate(eval(temp_fig).data):
        trace.marker.colors = [color_map[l] for l in trace.labels]
    eval(temp_fig).show()

    exec(f"{final_data}=rfm_q_y.copy()")
    fig_dict[f"Year: {years[ind]}"]=[eval(temp_fig),rfm_q_y]
    ind=ind+1
rfm_dict[title]=fig_dict

#     print(rfm_q_y.to_string())


In [285]:
main_fig_num=fig_num
print(main_fig_num)

165


In [286]:
# Combinig all years Customer Segment Data into one dataframe for comparing
temp='rfm_q_'+str(start_years[0])
rfm_q_mix=eval(temp)[["CustomerName","Customer_segment"]].copy()
rfm_q_mix=rfm_q_mix.rename(columns={"Customer_segment":f"Customer_segment_{start_years[0]}"})
for y in start_years[1:]:
    temp='rfm_q_'+str(y)
    rfm_q_mix = pd.merge(rfm_q_mix,eval(temp)[['CustomerName','Customer_segment']],how='outer', on = 'CustomerName')
    rfm_q_mix=rfm_q_mix.rename(columns={"Customer_segment":f"Customer_segment_{y}"})

rfm_q_mix

CustomerName    Customer_segment_14 Customer_segment_15   
0        Jas O'Carroll          Lost Customer       Lost Customer  \
1         Trudy Glocke  Medium Value Customer                 NaN   
2           Alex Avila  Medium Value Customer  Low Value Customer   
3           Karen Bern          Lost Customer                 NaN   
4    Dorothy Dickinson     Low Value Customer       Lost Customer   
..                 ...                    ...                 ...   
788     Jocasta Rupert                    NaN                 NaN   
789  Patricia Hirasaki                    NaN                 NaN   
790      Theresa Coyne                    NaN                 NaN   
791       Jenna Caffey                    NaN                 NaN   
792    Mitch Gastineau                    NaN                 NaN   

       Customer_segment_16  Customer_segment_17    Customer_segment_18  
0    Medium Value Customer  High Value Customer     Low Value Customer  
1      High Value Customer                  NaN     Low Value Customer  
2    Medium Value Customer                  NaN  Medium Value Customer  
3       Low Value Customer                  NaN  Medium Value Customer  
4                      NaN   Low Value Customer  Medium Value Customer  
..                     ...                  ...                    ...  
788                    NaN                  NaN     Low Value Customer  
789                    NaN                  NaN  Medium Value Customer  
790                    NaN                  NaN    High Value Customer  
791                    NaN                  NaN    High Value Customer  
792                    NaN                  NaN     Low Value Customer  

[793 rows x 6 columns]

In [287]:
# # Removing Customer whose Segemnt is not changed
# rfm_q_mix_diff=rfm_q_mix.copy()
# for y in start_years[1:]:
#     rm=rfm_q_mix_diff[(rfm_q_mix_diff[f"Customer_segment_{int(y)-1}"]==rfm_q_mix_diff[f"Customer_segment_{y}"])].index
#     rfm_q_mix_diff=rfm_q_mix_diff.drop(rm)
# rfm_q_mix_diff


In [288]:
rfm_q_mix_merged = pd.merge(rfm_q_mix, rfm_q[['CustomerName','Customer_segment']], on='CustomerName',how='outer')
rfm_q_mix_merged.rename(columns={'Customer_segment': 'Customer_segment_all'}, inplace=True)
rfm_q_mix_merged

CustomerName    Customer_segment_14 Customer_segment_15   
0        Jas O'Carroll          Lost Customer       Lost Customer  \
1         Trudy Glocke  Medium Value Customer                 NaN   
2           Alex Avila  Medium Value Customer  Low Value Customer   
3           Karen Bern          Lost Customer                 NaN   
4    Dorothy Dickinson     Low Value Customer       Lost Customer   
..                 ...                    ...                 ...   
788     Jocasta Rupert                    NaN                 NaN   
789  Patricia Hirasaki                    NaN                 NaN   
790      Theresa Coyne                    NaN                 NaN   
791       Jenna Caffey                    NaN                 NaN   
792    Mitch Gastineau                    NaN                 NaN   

       Customer_segment_16  Customer_segment_17    Customer_segment_18   
0    Medium Value Customer  High Value Customer     Low Value Customer  \
1      High Value Customer                  NaN     Low Value Customer   
2    Medium Value Customer                  NaN  Medium Value Customer   
3       Low Value Customer                  NaN  Medium Value Customer   
4                      NaN   Low Value Customer  Medium Value Customer   
..                     ...                  ...                    ...   
788                    NaN                  NaN     Low Value Customer   
789                    NaN                  NaN  Medium Value Customer   
790                    NaN                  NaN    High Value Customer   
791                    NaN                  NaN    High Value Customer   
792                    NaN                  NaN     Low Value Customer   

      Customer_segment_all  
0    Medium Value Customer  
1    Medium Value Customer  
2      High Value Customer  
3       Low Value Customer  
4            Lost Customer  
..                     ...  
788          Lost Customer  
789          Lost Customer  
790     Low Value Customer  
791     Low Value Customer  
792     Low Value Customer  

[793 rows x 7 columns]

In [289]:
# Finding the Customer who made there first purchase in years 14-15 and similary for all other years
title="(Pie) Customer Who Joined in a year and there segment in end of that year"
fig_dict={}
size=len(start_years)
i=0
fig_num=main_fig_num
while i<size:
    temp='rfm_join_'+str(start_years[i])
    work_data=rfm_q_mix_merged.copy()
    j=0
    while j<=i:
        if j==i:
            work_data=work_data[work_data[f"Customer_segment_{start_years[j]}"].notnull()]
        else:
            work_data=work_data[work_data[f"Customer_segment_{start_years[j]}"].isnull()]
        j=j+1
    work_data=work_data[["CustomerName",f"Customer_segment_{start_years[i]}"]]
    exec(f"{temp}=work_data.copy()")
    rfm_segment_counts = work_data[f'Customer_segment_{start_years[i]}'].value_counts()
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.pie(eval(temp), values=rfm_segment_counts.values, names=rfm_segment_counts.index)")
    exec(f"{temp_fig}.update_layout(title='Customer Who Joined in {years[i]} and there segment in end of {years[i]}',title_font_size=24)")
    for x,trace in enumerate(eval(temp_fig).data):
        trace.marker.colors = [color_map[l] for l in trace.labels]

    eval(temp_fig).show()
    fig_dict[f"Year: {years[i]}"]=[eval(temp_fig),eval(temp)]
    i=i+1
rfm_dict[title]=fig_dict

In [290]:
main_fig_num=fig_num
print(main_fig_num)

170


In [291]:
# Finding the Customer who made there first purchase in years 15-16 and similary for all other years
# Then plotting such customer with there segment in present year considering overall data
title="(Pie) Customer Who Joined in a year and there current segment"
fig_dict={}
size=len(start_years)
i=0
fig_num=main_fig_num
while i<size:
    temp='rfm_join_'+str(start_years[i])
    work_data=rfm_q_mix_merged.copy()
    j=0
    while j<=i:
        if j==i:
            work_data=work_data[work_data[f"Customer_segment_{start_years[j]}"].notnull()]
        else:
            work_data=work_data[work_data[f"Customer_segment_{start_years[j]}"].isnull()]
        j=j+1
#     print(f"\n\n\nCustomer Who Joined in {years[i]} :\n")
    extra_data_transfer=work_data[["CustomerName",f"Customer_segment_{start_years[i]}","Customer_segment_all"]]
    work_data=work_data[["CustomerName",f"Customer_segment_all"]]
    exec(f"{temp}=work_data.copy()")
    rfm_segment_counts = work_data[f'Customer_segment_all'].value_counts()
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.pie(rfm_mix, values=rfm_segment_counts.values, names=rfm_segment_counts.index,color_discrete_map=color_map)")
    exec(f"{temp_fig}.update_layout(title='Customer who joined in {years[i]} and there current segment',title_font_size=24)")
    for x,trace in enumerate(eval(temp_fig).data):
        trace.marker.colors = [color_map[l] for l in trace.labels]

    eval(temp_fig).show()
    fig_dict[f"Year: {years[i]}"]=[eval(temp_fig),extra_data_transfer]
    i=i+1
rfm_dict[title]=fig_dict

In [292]:
main_fig_num=fig_num
print(main_fig_num)

175


In [293]:
# Getting all detail of a particular segment like Top Segment and then finding the trend of customer changing segment from Top to other segment in its next year
# This can help to understand about how well we retain our customer over the year
title="(Pie) Customer Who Changed There Segment"
fig_dict={}
size=len(start_years)
i=1
fig_num=main_fig_num

while i<size:
    temp='rfm_join_'+str(start_years[i])
    work_data=rfm_q_mix.copy()
    rm=eval(temp).index
    work_data=work_data.drop(rm)
    for seg in Customer_Segment:
        temp2=work_data.copy()
        temp2['Customer_segment_'+start_years[int(i)]] = temp2['Customer_segment_'+start_years[int(i)]].fillna('NO Purchase')
        temp2=temp2[temp2['Customer_segment_'+start_years[int(i)-1]]==seg]
        rfm_segment_counts = temp2['Customer_segment_'+start_years[int(i)]].value_counts()
        temp_fig='fig_'+str(fig_num)
        fig_num=fig_num+1;
        exec(f"{temp_fig}=go.Figure()")
        exec(f"{temp_fig} = px.pie(temp2, values=rfm_segment_counts.values, names=rfm_segment_counts.index,color_discrete_map=color_map)")
        exec(f"{temp_fig}.update_layout(title='{seg} Customers of {years[int(i)-1]} who changed in {years[i]}',title_font_size=24)")
        for x,trace in enumerate(eval(temp_fig).data):
            trace.marker.colors = [color_map[l] for l in trace.labels]

        eval(temp_fig).show()
        print(temp2)
        print('\n\n\n\n\n\n')
        fig_dict[f"Segment:{seg}, Year:{years[int(i)-1]}"]=[eval(temp_fig),temp2]
    i=i+1
rfm_dict[title]=fig_dict

          CustomerName Customer_segment_14    Customer_segment_15   
46       Filia McAdams        Top Customer     Low Value Customer  \
53      Craig Molinari        Top Customer    High Value Customer   
54         Aimee Bixby        Top Customer            NO Purchase   
75   Delfina Latchford        Top Customer            NO Purchase   
80    Natalie Fritzler        Top Customer            NO Purchase   
83     Chris Selesnick        Top Customer    High Value Customer   
94     Shirley Daniels        Top Customer    High Value Customer   
97        Xylona Preis        Top Customer  Medium Value Customer   
98        Hunter Lopez        Top Customer     Low Value Customer   
101      Toby Swindell        Top Customer          Lost Customer   
105       Brian Dahlen        Top Customer            NO Purchase   
112      Maria Etezadi        Top Customer            NO Purchase   
116      Phillina Ober        Top Customer            NO Purchase   

       Customer_segment_16    Cus

            CustomerName  Customer_segment_14    Customer_segment_15   
5          Guy Armstrong  High Value Customer          Lost Customer  \
28      Kristen Hastings  High Value Customer            NO Purchase   
30          Matt Connell  High Value Customer     Low Value Customer   
31      Sample Company A  High Value Customer            NO Purchase   
33           Sean Miller  High Value Customer            NO Purchase   
35        Christine Phan  High Value Customer            NO Purchase   
39          Alan Shonely  High Value Customer          Lost Customer   
49         Kean Thornton  High Value Customer           Top Customer   
52         Aaron Bergman  High Value Customer            NO Purchase   
58        Jill Stevenson  High Value Customer            NO Purchase   
62      Shahid Collister  High Value Customer            NO Purchase   
79   Marina Lichtenstein  High Value Customer           Top Customer   
84           Neil Ducich  High Value Customer     Low Value Cust

               CustomerName    Customer_segment_14    Customer_segment_15   
1              Trudy Glocke  Medium Value Customer            NO Purchase  \
2                Alex Avila  Medium Value Customer     Low Value Customer   
9               Mark Packer  Medium Value Customer     Low Value Customer   
13   Christina VanderZanden  Medium Value Customer     Low Value Customer   
17       Christina Anderson  Medium Value Customer          Lost Customer   
18             Annie Zypern  Medium Value Customer            NO Purchase   
21        Patrick O'Donnell  Medium Value Customer     Low Value Customer   
23            Beth Fritzler  Medium Value Customer            NO Purchase   
27              Gary McGarr  Medium Value Customer  Medium Value Customer   
34           Bradley Nguyen  Medium Value Customer    High Value Customer   
37            Mark Haberlin  Medium Value Customer            NO Purchase   
38            Kristina Nunn  Medium Value Customer            NO Purchase   

           CustomerName Customer_segment_14    Customer_segment_15   
4     Dorothy Dickinson  Low Value Customer          Lost Customer  \
6          Dorris liebe  Low Value Customer     Low Value Customer   
11      Mike Gockenbach  Low Value Customer            NO Purchase   
12        Daniel Raglin  Low Value Customer          Lost Customer   
14      Damala Kotsonis  Low Value Customer     Low Value Customer   
25        Craig Carroll  Low Value Customer  Medium Value Customer   
29    Cassandra Brandow  Low Value Customer          Lost Customer   
32        Eileen Kiefer  Low Value Customer            NO Purchase   
36         Quincy Jones  Low Value Customer  Medium Value Customer   
40     Neil Französisch  Low Value Customer     Low Value Customer   
42            Dean Katz  Low Value Customer            NO Purchase   
44   Christine Kargatis  Low Value Customer  Medium Value Customer   
45       Kelly Andreada  Low Value Customer          Lost Customer   
48  Chloris Kastensm

        CustomerName Customer_segment_14    Customer_segment_15   
0      Jas O'Carroll       Lost Customer          Lost Customer  \
3         Karen Bern       Lost Customer            NO Purchase   
7     Susan Gilcrest       Lost Customer            NO Purchase   
8       Kunst Miller       Lost Customer           Top Customer   
10       Nat Carroll       Lost Customer  Medium Value Customer   
15     Cindy Stewart       Lost Customer            NO Purchase   
16  Jonathan Doherty       Lost Customer           Top Customer   
19       Carlos Daly       Lost Customer            NO Purchase   
20     Maurice Satty       Lost Customer     Low Value Customer   
22        Bruce Geld       Lost Customer            NO Purchase   
24     Vivian Mathis       Lost Customer            NO Purchase   
26       Thomas Seio       Lost Customer    High Value Customer   
47   Richard Bierner       Lost Customer    High Value Customer   

      Customer_segment_16  Customer_segment_17    Customer_se

...

           CustomerName    Customer_segment_14    Customer_segment_15   
8          Kunst Miller          Lost Customer           Top Customer  \
16     Jonathan Doherty          Lost Customer           Top Customer   
34       Bradley Nguyen  Medium Value Customer    High Value Customer   
41         Rick Bensley  Medium Value Customer    High Value Customer   
72       Linda Cazamias  Medium Value Customer                    NaN   
77    Barry Französisch     Low Value Customer                    NaN   
97         Xylona Preis           Top Customer  Medium Value Customer   
142       Joe Kamberova                    NaN    High Value Customer   
156      Arianne Irving                    NaN    High Value Customer   
201          Jill Fjeld                    NaN     Low Value Customer   
235        Rob Williams                    NaN     Low Value Customer   
243    Zuschuss Carroll                    NaN    High Value Customer   
276       William Brown                    NaN    H

       CustomerName Customer_segment_14 Customer_segment_15   
0     Jas O'Carroll       Lost Customer       Lost Customer  \
12    Daniel Raglin  Low Value Customer       Lost Customer   
15    Cindy Stewart       Lost Customer                 NaN   
20    Maurice Satty       Lost Customer  Low Value Customer   
22       Bruce Geld       Lost Customer                 NaN   
..              ...                 ...                 ...   
763  Justin Ellison                 NaN                 NaN   
771        Jim Sink                 NaN                 NaN   
772   Jill Matthias                 NaN                 NaN   
776      Max Ludwig                 NaN                 NaN   
784      Sean Wendt                 NaN                 NaN   

       Customer_segment_16  Customer_segment_17    Customer_segment_18  
0    Medium Value Customer  High Value Customer     Low Value Customer  
12     High Value Customer  High Value Customer     Low Value Customer  
15   Medium Value Custom

               CustomerName    Customer_segment_14    Customer_segment_15   
6              Dorris liebe     Low Value Customer     Low Value Customer  \
13   Christina VanderZanden  Medium Value Customer     Low Value Customer   
14          Damala Kotsonis     Low Value Customer     Low Value Customer   
31         Sample Company A    High Value Customer                    NaN   
36             Quincy Jones     Low Value Customer  Medium Value Customer   
..                      ...                    ...                    ...   
748         Ted Butterfield                    NaN                    NaN   
750                Ken Dana                    NaN                    NaN   
758             Rob Beeghly                    NaN                    NaN   
761       Charles McCrossin                    NaN                    NaN   
777            Alex Grayson                    NaN                    NaN   

     Customer_segment_16    Customer_segment_17    Customer_segment_18  
6 

          CustomerName    Customer_segment_14    Customer_segment_15   
4    Dorothy Dickinson     Low Value Customer          Lost Customer  \
7       Susan Gilcrest          Lost Customer                    NaN   
10         Nat Carroll          Lost Customer  Medium Value Customer   
19         Carlos Daly          Lost Customer                    NaN   
21   Patrick O'Donnell  Medium Value Customer     Low Value Customer   
..                 ...                    ...                    ...   
778       Larry Blacks                    NaN                    NaN   
779     Anemone Ratner                    NaN                    NaN   
780       Lela Donovan                    NaN                    NaN   
781         Roy Skaria                    NaN                    NaN   
783          Ed Ludwig                    NaN                    NaN   

    Customer_segment_16 Customer_segment_17    Customer_segment_18  
4                   NaN  Low Value Customer  Medium Value Customer

          CustomerName    Customer_segment_14  Customer_segment_15   
5        Guy Armstrong    High Value Customer        Lost Customer  \
37       Mark Haberlin  Medium Value Customer                  NaN   
45      Kelly Andreada     Low Value Customer        Lost Customer   
76      Michael Nguyen     Low Value Customer  High Value Customer   
86    Tom Boeckenhauer    High Value Customer  High Value Customer   
..                 ...                    ...                  ...   
744      Tony Molinari                    NaN                  NaN   
745  Michelle Lonsdale                    NaN                  NaN   
753      Roland Murray                    NaN                  NaN   
759       Carl Jackson                    NaN                  NaN   
764      Sally Knutson                    NaN                  NaN   

    Customer_segment_16 Customer_segment_17    Customer_segment_18  
5    Low Value Customer       Lost Customer  Medium Value Customer  
37        Lost Custom

In [294]:
main_fig_num=fig_num
print(main_fig_num)

195


In [295]:
main_data_dict["RFM Analysis"]=rfm_dict

In [296]:
# This show us the trend in change in customer segment in one year for each segment seperately
# The first bar of Top Segment Plot means the condition of segment of TOP customer of 14-15 in 15-16 
title="Stacked Plot of Customer Segment Change in next Year"
fig_dict={}
fig_num=main_fig_num

for seg in Customer_Seg:
    i=1;
    temp="rfm_nextyear_multilevel_"+str(seg)
    exec(f"{temp}=pd.DataFrame()")
    for k,v in main_data_dict["RFM Analysis"]["(Pie) Customer Who Changed There Segment"].items():
        if seg in k:
            temp2=v[1][['CustomerName','Customer_segment_'+start_years[int(i)]]]
            temp2.rename(columns = {f"Customer_segment_{start_years[int(i)]}":f"Customer_segment_{start_years[int(i-1)]}"}, inplace = True)
            i=i+1
            temp_col_name = temp2.iloc[:, 1]
            segment_counts = temp2.iloc[:, 1].groupby(temp_col_name).size()
            total_count = segment_counts.sum()
            segment_percents = segment_counts / total_count * 100
            new_df = pd.DataFrame({
                'Segment': segment_percents.index,
                temp2.columns[1]: segment_percents.values
            })
            if eval(temp).empty:
                exec(f"{temp}=new_df")
            else:
                exec(f"{temp}=pd.merge({temp}, new_df,on='Segment',how='outer')")
    print(eval(temp))
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    x_values = eval(temp).columns[1:]
    y_values = eval(temp)['Segment'].unique()
    df_melt = pd.melt(eval(temp), id_vars=['Segment'], var_name='Year', value_name='Percent')
    
#    Creating Label for X axix of out plot
    year_labels = [label.split("_")[-1] for label in x_values]
    new_year_labels = [f"{year_labels[i]}-{int(year_labels[i])+1} to {int(year_labels[i])+1}-{int(year_labels[i])+2}" for i in range(len(year_labels))]
    ticktext = new_year_labels
    
    exec(f"{temp_fig} = px.bar(df_melt, x='Year', y='Percent', color='Segment', barmode='stack',color_discrete_map=color_map)")
    eval(temp_fig).update_layout(
        title = f"Stacked Segment: {seg}",
        xaxis_title = 'Year', 
        yaxis_title = 'Percent',
        xaxis=dict(
            tickmode='array',
            tickvals=x_values,
            ticktext=ticktext,
        ),)
    print(eval(temp_fig).show())
    fig_dict[f"Stacked Segment:{seg}, Next Year Segment"]=[eval(temp_fig),eval(temp)]
rfm_dict[title]=fig_dict

# Temp here tells that all "Top" cutomer of a year and there segment in its next year

                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            23.076923              20.3125  \
1          Lost Customer             7.692308               3.1250   
2     Low Value Customer            15.384615              25.0000   
3  Medium Value Customer             7.692308              17.1875   
4            NO Purchase            46.153846              25.0000   
5           Top Customer                  NaN               9.3750   

   Customer_segment_16  Customer_segment_17  
0            11.320755             9.615385  
1             7.547170            13.461538  
2            22.641509            30.769231  
3            20.754717            21.153846  
4            32.075472            19.230769  
5             5.660377             5.769231  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer                  8.0            14.035088  \
1          Lost Customer                 16.0             9.649123   
2     Low Value Customer                 16.0            29.824561   
3  Medium Value Customer                  4.0            12.280702   
4            NO Purchase                 48.0            26.315789   
5           Top Customer                  8.0             7.894737   

   Customer_segment_16  Customer_segment_17  
0            23.015873            20.666667  
1             4.761905             4.666667  
2            27.777778            26.666667  
3            19.047619            26.666667  
4            16.666667            14.666667  
5             8.730159             6.666667  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            14.705882            19.444444  \
1          Lost Customer             5.882353             3.472222   
2     Low Value Customer            14.705882            20.138889   
3  Medium Value Customer            17.647059            22.222222   
4            NO Purchase            41.176471            24.305556   
5           Top Customer             5.882353            10.416667   

   Customer_segment_16  Customer_segment_17  
0            13.548387            17.816092  
1             9.677419             7.471264  
2            30.322581            25.287356  
3            21.290323            24.712644  
4            18.709677            18.965517  
5             6.451613             5.747126  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer             6.060606            15.555556  \
1          Lost Customer            12.121212             8.888889   
2     Low Value Customer            12.121212            20.000000   
3  Medium Value Customer            21.212121            24.444444   
4            NO Purchase            39.393939            26.666667   
5           Top Customer             9.090909             4.444444   

   Customer_segment_16  Customer_segment_17  
0            17.032967            17.676768  
1             9.340659             4.040404  
2            21.428571            29.797980  
3            24.175824            23.737374  
4            23.626374            17.171717  
5             4.395604             7.575758  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            15.384615            14.492754  \
1          Lost Customer             7.692308            11.594203   
2     Low Value Customer             7.692308            21.739130   
3  Medium Value Customer             7.692308            15.942029   
4            NO Purchase            46.153846            30.434783   
5           Top Customer            15.384615             5.797101   

   Customer_segment_16  Customer_segment_17  
0            16.666667            23.529412  
1            10.606061             8.823529  
2            15.151515            17.647059  
3            28.787879            22.058824  
4            19.696970            16.176471  
5             9.090909            11.764706  


None


In [297]:
main_fig_num=fig_num
print(main_fig_num)



200


In [298]:
# This show us the trend in change in customer segment in one year for each segment seperately
# The first bar of Top Segment Plot means the condition of segment of TOP customer of 14-15 in today
title="Stacked Plot of Customer Segment Change in current Year"
fig_dict={}
fig_num=main_fig_num
size=len(start_years)-1
for seg in Customer_Seg:
    i=0
    temp="rfm_finalyear_multilevel_"+str(seg)
    exec(f"{temp}=pd.DataFrame()")
    for k,v in main_data_dict["RFM Analysis"]["(Pie) Customer Who Changed There Segment"].items():
        if seg in k:
            temp2=v[1][['CustomerName','Customer_segment_'+start_years[int(size)]]]
            temp2.rename(columns = {f"Customer_segment_{start_years[int(size)]}":f"Customer_segment_{start_years[int(i)]}"}, inplace = True)
            i=i+1
            temp_col_name = temp2.iloc[:, 1]
            segment_counts = temp2.iloc[:, 1].groupby(temp_col_name).size()
            total_count = segment_counts.sum()
            segment_percents = segment_counts / total_count * 100
            new_df = pd.DataFrame({
                'Segment': segment_percents.index,
                temp2.columns[1]: segment_percents.values
            })
            if eval(temp).empty:
                exec(f"{temp}=new_df")
            else:
                exec(f"{temp}=pd.merge({temp}, new_df,on='Segment',how='outer')")
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    x_values = eval(temp).columns[1:]
    y_values = eval(temp)['Segment'].unique()
    df_melt = pd.melt(eval(temp), id_vars=['Segment'], var_name='Year', value_name='Percent')
    
    year_labels = [label.split("_")[-1] for label in x_values]
    new_year_labels = [f"{year_labels[i]}-{int(year_labels[i])+1} to Current Date" for i in range(len(year_labels))]
    ticktext = new_year_labels
    
    exec(f"{temp_fig} = px.bar(df_melt, x='Year', y='Percent', color='Segment', barmode='stack',color_discrete_map=color_map)")
    eval(temp_fig).update_layout(
        title = f"Stacked Segment: {seg}",
        xaxis_title = 'Year', 
        yaxis_title = 'Percent',
        xaxis=dict(
            tickmode='array',
            tickvals=x_values,
            ticktext=ticktext,
        ),)
    print(eval(temp_fig).show())
    print(eval(temp))
    fig_dict[f"Stacked Segment:{seg}, Current Segment"]=[eval(temp_fig),eval(temp)]
rfm_dict[title]=fig_dict



None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            16.666667            24.074074  \
1     Low Value Customer            33.333333            27.777778   
2  Medium Value Customer            41.666667            31.481481   
3           Top Customer             8.333333             7.407407   
4          Lost Customer                  NaN             9.259259   
5            NO Purchase                  NaN                  NaN   

   Customer_segment_16  Customer_segment_17  
0            30.952381             9.615385  
1            30.952381            30.769231  
2            19.047619            21.153846  
3            14.285714             5.769231  
4             4.761905            13.461538  
5                  NaN            19.230769  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer             9.090909            16.666667  \
1          Lost Customer             4.545455             7.291667   
2     Low Value Customer            36.363636            36.458333   
3  Medium Value Customer            36.363636            28.125000   
4           Top Customer            13.636364            11.458333   
5            NO Purchase                  NaN                  NaN   

   Customer_segment_16  Customer_segment_17  
0            17.307692            20.666667  
1             7.692308             4.666667  
2            38.461538            26.666667  
3            32.692308            26.666667  
4             3.846154             6.666667  
5                  NaN            14.666667  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            10.714286            20.353982  \
1          Lost Customer             3.571429             6.194690   
2     Low Value Customer            39.285714            38.053097   
3  Medium Value Customer            39.285714            26.548673   
4           Top Customer             7.142857             8.849558   
5            NO Purchase                  NaN                  NaN   

   Customer_segment_16  Customer_segment_17  
0            25.000000            17.816092  
1             7.258065             7.471264  
2            31.451613            25.287356  
3            28.225806            24.712644  
4             8.064516             5.747126  
5                  NaN            18.965517  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer            23.076923            24.489796  \
1          Lost Customer             7.692308             6.122449   
2     Low Value Customer            46.153846            34.013605   
3  Medium Value Customer            23.076923            24.489796   
4           Top Customer                  NaN            10.884354   
5            NO Purchase                  NaN                  NaN   

   Customer_segment_16  Customer_segment_17  
0            21.710526            17.676768  
1             9.868421             4.040404  
2            31.578947            29.797980  
3            25.000000            23.737374  
4            11.842105             7.575758  
5                  NaN            17.171717  


None
                 Segment  Customer_segment_14  Customer_segment_15   
0    High Value Customer             9.090909            18.965517  \
1          Lost Customer             9.090909            12.068966   
2     Low Value Customer            45.454545            25.862069   
3  Medium Value Customer            18.181818            37.931034   
4           Top Customer            18.181818             5.172414   
5            NO Purchase                  NaN                  NaN   

   Customer_segment_16  Customer_segment_17  
0            15.094340            23.529412  
1             7.547170             8.823529  
2            32.075472            17.647059  
3            37.735849            22.058824  
4             7.547170            11.764706  
5                  NaN            16.176471  


In [299]:
main_fig_num=fig_num
print(main_fig_num)

205


In [300]:
main_data_dict["RFM Analysis"]=rfm_dict

In [301]:
# Customer Retention
if cdict['CustomerName'] and cdict['BillDate']:
    print(1)

1


In [302]:
# Customer Churn :Customer churn is the proportion of customers that leave during a given time period
# Customer Retention :Customer Retention is the ability of a company to retain its customers during a given time period
# Cohort Analysis : Person that is your customer for 3 years behaves differently than a person that is a customer since 1 month.
# A Cohort Analysis breaks the data up in related groups rather than looking at all the customers as one unit within a defined time-span.

In [303]:
# This Plot Contain data for each year seperate so the customer can repeate over year as when in next year customer customer back he will be a new customer in data
# Making copy of orignial data to work
fig_dict={}
title=f"Retention Analysis"
ind=0
fig_num=main_fig_num
for y in start_years:
    temp='df_'+str(y)
    ret=eval(temp).copy()
    # We Do retention analysis on different months so to differentiate each day of
    # a month we just make the date of each month of each year as 1
    def get_month(x):
        return dt.datetime(x.year, x.month, 1)
    
    # ret['BillDate'] now contain the date as 1 for each BillDate
    ret['BillDate'] = ret['BillDate'].apply(get_month)

    # After this grouping contain all the billdate after the data is grouped using Name
    grouping = ret.groupby('CustomerName')['BillDate']
    # CohortDate will contain the min date of a cutomer from its group means it will be his first purchase date
    ret['CohortDate'] = grouping.transform('min')
#     print(ret[['BillDate','Name','CohortDate']])
    # This bill_year will contain year of each bill date and bill month contain month of each billdate
    bill_year, bill_month = get_year_int(ret, 'BillDate')
    
    # This cohort_year will contain year of each cohortdate and cohortmonth contain month of each cohortdate
    cohort_year, cohort_month = get_year_int(ret, 'CohortDate')

    # Calculate difference in years
    years_diff = bill_year - cohort_year

    # Calculate difference in months
    months_diff = bill_month - cohort_month

    # Extract the difference in months from all previous values
    ret['CohortIndex'] = years_diff * 12 + months_diff
    # Groupby with two variable will check all different pair of both variable means it will consider each pair of the variable as one data item
    grouping = ret.groupby(['CohortDate', 'CohortIndex'])
    
    # Count the number of unique values per Customer
    cohort_data = grouping['CustomerName'].apply(pd.Series.nunique).reset_index()
    # Create a pivot
    cohort_counts = cohort_data.pivot(index='CohortDate', columns='CohortIndex', values='CustomerName')
    
    # Select the first column and store it to cohort_sizes
    cohort_sizes = cohort_counts.iloc[:,0]
    
    # Divide the cohort count by cohort sizes along the rows
#     retention = cohort_counts.divide(cohort_sizes, axis=0)*100
    retention = cohort_counts
#     Saving retention as dataframe 
    temp_name='ret_'+str(y)
    exec(f"{temp_name} = pd.DataFrame(retention)")
    
    
    # Create list of month names for visualisation
    month_list = retention.reset_index()['CohortDate']

    def get_month_name(x):
       return dt.datetime.strftime(x, '%b-%y')
  
    month_list = month_list.apply(get_month_name)
    
    
    
#     We will not modify our dataframe for having a diffence in place where there is actually no customer vs place where data is not present/provided.
#     We will all extra row column to complete the dataframe 
#     0 represent that there are actually no cutomer in that section
#     -1/Nan represent that data is not procided
    
    # Initialize inches plot figure
    exec(f"{temp_name} = {temp_name}.reset_index(drop=False)")
    exec(f"{temp_name}.fillna(0, inplace=True)")
    
    
    # Define the number of blocks to modify in each row
    n_blocks = min(len(eval(temp_name).columns), len(eval(temp_name)) - 1)

    # Loop over each row and modify the appropriate number of blocks
    for i in range(1, n_blocks + 1):
        eval(temp_name).iloc[i, -i:] = -1


    exec(f"{temp_name} = {temp_name}.replace(-1, np.nan)")
      
    all_cols = [i for i in range(0, 12)]
    existing_cols = eval(temp_name).columns.tolist()
    missing_cols = list(set(all_cols) - set(existing_cols))
    for col in missing_cols:
        eval(temp_name)[col] = np.nan    
    
    last_date = pd.to_datetime(eval(temp_name)['CohortDate']).max()
    last_month = int(datetime.strftime(last_date, "%m"))
    last_year = int(datetime.strftime(last_date, "%Y"))
    all_row=[]
    if last_month<=3 :
        temp_val=4
        while temp_val<=12:
            date_obj = datetime(last_year-1,temp_val,1)
            dt64 = np.datetime64(date_obj)
            dt64=pd.to_datetime(dt64)
            dt64 = dt64.strftime('%Y-%m-%d')
            all_row.append(dt64)
            temp_val=temp_val+1
        temp_val=1
        while temp_val<=3:
            date_obj = datetime(last_year,temp_val,1)
            dt64 = np.datetime64(date_obj)
            dt64=pd.to_datetime(dt64)
            dt64 = dt64.strftime('%Y-%m-%d')
            all_row.append(dt64)
            temp_val=temp_val+1
            
        
    else:
        temp_val=4
        while temp_val<=12:
            date_obj = datetime(last_year,temp_val,1)
            dt64 = np.datetime64(date_obj)
            dt64=pd.to_datetime(dt64)
            dt64 = dt64.strftime('%Y-%m-%d')
            all_row.append(dt64)
            temp_val=temp_val+1
        temp_val=1
        while temp_val<=3:
            date_obj = datetime(last_year+1,temp_val,1)
            dt64 = np.datetime64(date_obj)
            dt64=pd.to_datetime(dt64)
            dt64 = dt64.strftime('%Y-%m-%d')
            all_row.append(dt64)
            temp_val=temp_val+1
        
                 
    all_row = np.array(all_row).astype('datetime64')
    for temp_row in all_row:
        if not (eval(temp_name)['CohortDate'].isin([str(temp_row)])).any():
            new_row = pd.DataFrame({"CohortDate": temp_row, **{col: np.nan for col in eval(temp_name).columns[1:]}}, index=[0])
            exec(f"{temp_name}=pd.concat([{temp_name},new_row], ignore_index=True)")
    
    exec(f"{temp_name} = {temp_name}.sort_values('CohortDate')")
    exec(f"{temp_name} = {temp_name}.reset_index(drop=True)")
    
    
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.imshow({temp_name}.set_index('CohortDate'), y={temp_name}['CohortDate'],width=800,height=800,color_continuous_scale=heatmap_color_scheme_low,text_auto=True)")
    exec(f"{temp_fig}.update_layout(margin=dict(t=200, b=100),title='{years[ind]} Retention Analysis (Considering Yearly Data)',title_font_size=24,xaxis_side='top')")
    eval(temp_fig).show();
    fig_dict[f"Year: {years[ind]}"]=[eval(temp_fig),{temp_name}]
    ind=ind+1
ret_dict[title]=fig_dict

In [304]:
main_fig_num=fig_num
print(main_fig_num)

210


In [305]:
title=f"Month-wise Retention Analysis"
fig_dict={}
i=0
fig_num=main_fig_num
for m in months:
    num=12
    temp='ret_'+str(m)
    exec(f"{temp}=pd.DataFrame()")
    
    for y in start_years:
        temp2='ret_'+str(y)
        exec(f"{temp2} = {temp2}.replace(np.nan,-1)")
        row = eval(temp2).iloc[i]
        row=row.iloc[1:]
        row=row.tolist()
        row = [value for value in row if not math.isnan(value)]
        row = [round(value, 1) for value in row]
#         print(f"Row : {row}\n")
        if eval(temp).empty:
            new_months = list(range(0,num))
            exec(f"{temp}=pd.DataFrame(columns=list(range(num)))")
            exec(f"{temp}.loc[len({temp})] = row")
        else:
            exec(f"{temp}.loc[len({temp})] = row")
    eval(temp).insert(0, 'Year', short_years, True)
    exec(f"{temp} = {temp}.replace(-1,np.nan)")
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.imshow(eval(temp).set_index('Year'), y=eval(temp)['Year'],color_continuous_scale=heatmap_color_scheme_high,text_auto=True)")
    exec(f"{temp_fig}.update_layout(margin=dict(t=200, b=100),title='{months[i]} Retention Analysis (Considering Yearly Data)',title_font_size=24,xaxis_side='top')")
    eval(temp_fig).show()
    fig_dict[f"Month:{m}"]=[eval(temp_fig),eval(temp)]
    exec(f"{temp} = {temp}.replace(np.nan,-1)")
#     print(eval(temp))
    i=i+1
ret_dict[title]=fig_dict 

In [306]:
main_fig_num=fig_num
print(main_fig_num)

222


In [307]:
i=0
ret_avg_all=pd.DataFrame()
for m in months:
    temp='ret_'+str(m)
    temp2=eval(temp).copy()
    temp3='ret_avg_'+str(m)
    num_rows=temp2.shape[0]
    row_sum = temp2.iloc[:, 1:].sum(axis=0)/num_rows
    row_sum = pd.concat([pd.Series(['Average'], index=['Year']), row_sum])
    temp2 = pd.concat([temp2, pd.DataFrame([row_sum.values], columns=row_sum.index)], ignore_index=True)
    exec(f"{temp3}= temp2.copy()")
    exec(f"{temp3} = {temp3}.iloc[[-1]]")
    print(f"\n\nAverage Retention of {m} : ")
    print(eval(temp3).to_string())
    if ret_avg_all.empty:
        ret_avg_all=eval(temp3)
    else:
        ret_avg_all=pd.concat([ret_avg_all,eval(temp3)], axis=0)



Average Retention of Apr : 
      Year     0    1    2    3    4     5    6     7     8    9   10   11
5  Average  63.6  8.6  6.2  7.6  6.4  14.8  8.2  13.0  13.4  2.2  2.6  4.6


Average Retention of May : 
      Year     0    1    2    3     4    5     6     7    8    9   10   11
5  Average  59.0  5.6  6.6  6.4  14.0  6.6  14.8  10.2  4.2  1.8  4.8 -1.0


Average Retention of Jun : 
      Year     0    1    2    3    4     5     6    7    8    9   10   11
5  Average  53.8  4.0  4.4  9.8  4.4  12.0  10.4  0.4  1.6  5.8 -1.0 -1.0


Average Retention of Jul : 
      Year     0    1    2    3    4    5    6    7    8    9   10   11
5  Average  43.6  4.8  7.6  4.4  7.0  8.6  0.8  1.0  3.0 -1.0 -1.0 -1.0


Average Retention of Aug : 
      Year     0    1    2     3    4    5    6    7    8    9   10   11
5  Average  40.6  8.2  3.8  10.0  8.4  1.4  2.0  1.4 -1.0 -1.0 -1.0 -1.0


Average Retention of Sep : 
      Year     0    1     2     3    4    5    6    7    8    9   10   11
5  Avera

In [308]:
fig_num=main_fig_num
ret_avg_all_temp=ret_avg_all.copy()
ret_avg_all_temp = ret_avg_all_temp.reset_index(drop=True)
ret_avg_all_temp = ret_avg_all_temp.drop('Year', axis=1)
ret_avg_all_temp['Months']=pd.Series(months)
last_col = ret_avg_all_temp.columns[-1]
ret_avg_all_temp = ret_avg_all_temp[[last_col]+list(ret_avg_all_temp.columns[:-1])]
ret_avg_all_temp= ret_avg_all_temp.replace(-1,np.nan)
temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
exec(f"{temp_fig} = px.imshow(ret_avg_all_temp.set_index('Months'), y=ret_avg_all_temp['Months'],width=800,height=800,color_continuous_scale=heatmap_color_scheme_high,text_auto=True)")
exec(f"{temp_fig}.update_layout(margin=dict(l=0, r=0, t=200, b=100),title='Average Retention Analysis (Considering yearly data)',title_font_size=24,xaxis_side='top')")
eval(temp_fig).show()
fig_dict={}
fig_dict['Average']=[eval(temp_fig),ret_avg_all_temp]
ret_dict["Average Retention Analysis"]=fig_dict
# print(ret_avg_all_temp)
# print(ret_avg_all_temp['Months'])

In [309]:
main_fig_num=fig_num
print(main_fig_num)

223


In [310]:
main_data_dict["Retention Analysis (Considering Yearly Data)"]=ret_dict
ret_dict={}

In [311]:
# In above retention analysis there is one issue that we have considered yearly data so for plotting row of march we just have data of march as year ends on march and we are not able to analysis this month properly so now we will consider complete data which will provide detail about every month
# Also it consider all customer as new customer in next year

In [312]:
# All 12 months descriptive analysis on retention
# Doing this so that we can check analysis for each month as in above the last month do not have any analysis 

In [313]:
# Making copy of orignial data to work
ind=0
fig_num=main_fig_num
temp='df'
ret=eval(temp).copy()

# Getting this to have the last date for seperating missing data and data actually zero
first_date = pd.to_datetime(eval(temp)['BillDate']).min()
last_date = pd.to_datetime(eval(temp)['BillDate']).max()


# We Do retention analysis on different months so to differentiate each day of
# a month we just make the date of each month of each year as 1
def get_month(x):
    return dt.datetime(x.year, x.month, 1)
# print(ret)
    # ret['BillDate'] now contain the date as 1 for each BillDate
ret['BillDate'] = ret['BillDate'].apply(get_month)

    # After this grouping contain all the billdate after the data is grouped using Name
grouping = ret.groupby('CustomerName')['BillDate']
    # CohortDate will contain the min date of a cutomer from its group means it will be his first purchase date
ret['CohortDate'] = grouping.transform('min')

    # This bill_year will contain year of each bill date and bill month contain month of each billdate
bill_year, bill_month = get_year_int(ret, 'BillDate')

    # This cohort_year will contain year of each cohortdate and cohortmonth contain month of each cohortdate
cohort_year, cohort_month = get_year_int(ret, 'CohortDate')

    # Calculate difference in years
years_diff = bill_year - cohort_year

    # Calculate difference in months
months_diff = bill_month - cohort_month

    # Extract the difference in months from all previous values
ret['CohortIndex'] = years_diff * 12 + months_diff

    # Groupby with two variable will check all different pair of both variable means it will consider each pair of the variable as one data item
grouping = ret.groupby(['CohortDate', 'CohortIndex'])
    
    # Count the number of unique values per Customer
cohort_data = grouping['CustomerName'].apply(pd.Series.nunique).reset_index()
    
    # Create a pivot
cohort_counts = cohort_data.pivot(index='CohortDate', columns='CohortIndex', values='CustomerName')
    
    # Select the first column and store it to cohort_sizes
cohort_sizes = cohort_counts.iloc[:,0]
    
    # Divide the cohort count by cohort sizes along the rows
retention_per = cohort_counts.divide(cohort_sizes, axis=0)*100
retention_val = cohort_counts

# Retention in Cutomer Numbers
#Saving retention as dataframe 
temp_name='ret_extra_months'
exec(f"{temp_name} = pd.DataFrame(retention_val)")
    
    
# Create list of month names for visualisation
month_list = retention.reset_index()['CohortDate']

def get_month_name(x):
    return dt.datetime.strftime(x, '%b-%y')
  
month_list = month_list.apply(get_month_name)
exec(f"{temp_name} = {temp_name}.reset_index(drop=False)")

    
#     We will not modify our dataframe for having a diffence in place where there is actually no customer vs place where data is not present/provided.
#     We will all extra row column to complete the dataframe 
#     0 represent that there are actually no cutomer in that section
#     -1/Nan represent that data is not procided


first_month = int(datetime.strftime(first_date, "%m"))
first_year = int(datetime.strftime(first_date, "%Y"))
last_month = int(datetime.strftime(last_date, "%m"))
last_year = int(datetime.strftime(last_date, "%Y"))
last_missing_row=0
if last_month<=3:
    last_missing_row=3-last_month
else:
    last_missing_row=(12-last_month)+3
    

all_cols = [i for i in range(0,(len(years)*12))]
existing_cols = eval(temp_name).columns.tolist()
missing_cols = list(set(all_cols) - set(existing_cols))
for col in missing_cols:
    eval(temp_name)[col] = 0

all_row=[]
for sy in years:
    sy=sy.split('-')[0]
    temp_val=4
    while temp_val<=12:
        date_obj = datetime(int(sy),temp_val,1)
        dt64 = np.datetime64(date_obj)
        dt64=pd.to_datetime(dt64)
        dt64 = dt64.strftime('%Y-%m-%d')
        all_row.append(dt64)
        temp_val=temp_val+1
    temp_val=1
    while temp_val<=3:
        date_obj = datetime(int(sy)+1,temp_val,1)
        dt64 = np.datetime64(date_obj)
        dt64=pd.to_datetime(dt64)
        dt64 = dt64.strftime('%Y-%m-%d')
        all_row.append(dt64)
        temp_val=temp_val+1
    
new_temp_name = eval(temp_name)
all_row = np.array(all_row).astype('datetime64')
for temp_row in all_row:
    if not (new_temp_name['CohortDate'].isin([str(temp_row)])).any():
#         print(temp_row)
        temp_value = temp_row.astype(datetime)
        check_month = int(datetime.strftime(temp_value, "%m"))
        check_year = int(datetime.strftime(temp_value, "%Y"))
        if check_year<first_year or check_year>last_year or ((check_year==first_year)and(check_month<first_month)) or ((check_year==last_year)and(check_month>last_month)):
#             print(f"check_y : {check_year}  , check_m :{check_month}")
            new_row = pd.DataFrame({"CohortDate": temp_value, **{col: -1 for col in eval(temp_name).columns[1:]}}, index=[0])
            exec(f"{temp_name}=pd.concat([{temp_name},new_row], ignore_index=True)")
        else:
            new_row = pd.DataFrame({"CohortDate": temp_value, **{col: 0 for col in eval(temp_name).columns[1:]}}, index=[0])
            exec(f"{temp_name}=pd.concat([{temp_name},new_row], ignore_index=True)")
            
exec(f"{temp_name}['CohortDate'] = pd.to_datetime({temp_name}['CohortDate'])")
exec(f"{temp_name} = {temp_name}.sort_values('CohortDate')")

exec(f"{temp_name} = {temp_name}.reset_index(drop=True)")
    
# exec(f"{temp_name} = {temp_name}.reset_index(drop=False)")
exec(f"{temp_name}.fillna(0, inplace=True)")
    
# Define the number of blocks to modify in each row
n_blocks = min(len(eval(temp_name).columns), len(eval(temp_name)) - 1)

# Loop over each row and modify the appropriate number of blocks
for i in range(0, ((n_blocks + 1)-last_missing_row)):
    eval(temp_name).iloc[i, -(i+last_missing_row):] = -1

# print(eval(temp_name))
exec(f"{temp_name} = {temp_name}.replace(-1, np.nan)")

temp_fig='fig_'+str(fig_num)
fig_num=fig_num+1;
exec(f"{temp_fig}=go.Figure()")
exec(f"{temp_fig} = px.imshow(eval(temp_name).set_index('CohortDate'),y=eval(temp_name)['CohortDate'],width=800,height=800,color_continuous_scale=heatmap_color_scheme_low,text_auto=True)")
exec(f"{temp_fig}.update_layout(margin=dict(l=0, r=0, t=200, b=100),title='Overall Retention Analysis (Considering complete data)',title_font_size=24,xaxis_side='top')")
eval(temp_fig).show();
fig_dict={}
fig_dict["Overall"]=[eval(temp_fig),eval(temp_name)]
ret_dict["Overall Retention Analysis (Considering complete data)"]=fig_dict

In [314]:
main_fig_num=fig_num
print(main_fig_num)

224


In [315]:
ret_12_months=ret_extra_months.iloc[:,:13]
if ret_12_months['CohortDate'].dtype != 'datetime64[ns]':
    ret_12_months['CohortDate'] = pd.to_datetime(ret_12_months['CohortDate'])
ret_12_months.insert(0, 'Months', get_year_int(ret_12_months,'CohortDate')[1], True)
ret_12_months.insert(0, 'Year', get_year_int(ret_12_months,'CohortDate')[0], True)
ret_12_months=ret_12_months.drop('CohortDate',axis=1)
ret_12_months

Year  Months     0     1    2     3     4    5     6     7    8     9   
0   2014       4   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN  \
1   2014       5   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
2   2014       6   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
3   2014       7   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
4   2014       8   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
5   2014       9   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
6   2014      10   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
7   2014      11   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
8   2014      12   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
9   2015       1  30.0   2.0  0.0   2.0   2.0  0.0   2.0   3.0  3.0   3.0   
10  2015       2  25.0   4.0  2.0   1.0   0.0  2.0   2.0   4.0  3.0   3.0   
11  2015       3  63.0   4.0  2.0   8.0   7.0  0.0   7.0   5.0  6.0   6.0   
12  2015       4  53.0   6.0  1.0   3.0   2.0  8.0   5.0   9.0  8.0   1.0   
13  2015       5  55.0   5.0  5.0   4.0  10.0  2.0  11.0  10.0  4.0   3.0   
14  2015       6  47.0   2.0  1.0   4.0   2.0  9.0   8.0   1.0  4.0   6.0   
15  2015       7  43.0   6.0  5.0   0.0   5.0  8.0   2.0   0.0  8.0   2.0   
16  2015       8  50.0   8.0  3.0  11.0   5.0  3.0   4.0   2.0  5.0   3.0   
17  2015       9  68.0   9.0  8.0  11.0   1.0  2.0   8.0  10.0  9.0   2.0   
18  2015      10  43.0   3.0  5.0   1.0   3.0  4.0   5.0   4.0  3.0   4.0   
19  2015      11  63.0  14.0  0.0   3.0   5.0  4.0   2.0   6.0  3.0   5.0   
20  2015      12  49.0   2.0  4.0   4.0   2.0  2.0   4.0   6.0  5.0  10.0   
21  2016       1   8.0   0.0  1.0   0.0   1.0  0.0   2.0   0.0  0.0   1.0   
22  2016       2   8.0   0.0  1.0   0.0   0.0  1.0   0.0   3.0  0.0   0.0   
23  2016       3  17.0   1.0  1.0   3.0   1.0  1.0   3.0   1.0  2.0   1.0   
24  2016       4  12.0   0.0  0.0   1.0   0.0  1.0   2.0   2.0  0.0   0.0   
25  2016       5  12.0   0.0  0.0   1.0   2.0  0.0   2.0   2.0  1.0   1.0   
26  2016       6  12.0   1.0  1.0   4.0   1.0  3.0   2.0   0.0  1.0   3.0   
27  2016       7   8.0   0.0  0.0   2.0   3.0  1.0   0.0   2.0  0.0   0.0   
28  2016       8  13.0   3.0  1.0   2.0   4.0  0.0   0.0   0.0  0.0   1.0   
29  2016       9  17.0   2.0  4.0   1.0   4.0  1.0   3.0   2.0  1.0   0.0   
30  2016      10  10.0   0.0  4.0   0.0   0.0  1.0   0.0   1.0  0.0   1.0   
31  2016      11  11.0   1.0  1.0   0.0   0.0  0.0   1.0   1.0  2.0   2.0   
32  2016      12  13.0   1.0  0.0   1.0   2.0  2.0   0.0   3.0  1.0   3.0   
33  2017       1   6.0   1.0  0.0   1.0   0.0  1.0   1.0   1.0  0.0   1.0   
34  2017       2   2.0   0.0  1.0   0.0   0.0  0.0   0.0   0.0  1.0   1.0   
35  2017       3   6.0   0.0  3.0   0.0   3.0  0.0   1.0   1.0  1.0   1.0   
36  2017       4   8.0   2.0  0.0   1.0   2.0  4.0   0.0   1.0  0.0   2.0   
37  2017       5   7.0   0.0  1.0   2.0   1.0  1.0   2.0   1.0  2.0   1.0   
38  2017       6   7.0   1.0  2.0   2.0   0.0  1.0   1.0   0.0  0.0   1.0   
39  2017       7   2.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0   1.0   
40  2017       8   4.0   0.0  0.0   0.0   0.0  1.0   0.0   1.0  2.0   2.0   
41  2017       9   1.0   1.0  0.0   0.0   1.0  0.0   1.0   0.0  0.0   0.0   
42  2017      10   1.0   0.0  1.0   0.0   0.0  0.0   0.0   0.0  0.0   0.0   
43  2017      11   6.0   0.0  1.0   0.0   1.0  1.0   0.0   0.0  0.0   0.0   
44  2017      12   2.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0   0.0   
45  2018       1   0.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0   0.0   
46  2018       2   0.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0   0.0   
47  2018       3   3.0   0.0  0.0   1.0   1.0  1.0   0.0   1.0  0.0   0.0   
48  2018       4   1.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0   NaN   
49  2018       5   0.0   0.0  0.0   0.0   0.0  0.0   0.0   0.0  NaN   NaN   
50  2018       6   1.0   0.0  0.0   0.0   0.0  0.0   1.0   NaN  NaN   NaN   


In [316]:
month_map = {1: 'Jan', 2: 'Feb', 3: 'Mar', 4: 'Apr',
             5: 'May', 6: 'Jun', 7: 'Jul', 8: 'Aug',
             9: 'Sep', 10: 'Oct', 11: 'Nov', 12: 'Dec'}

def get_month_name(month_number):
    return month_number.map(month_map)



In [317]:
fig_num=main_fig_num
fig_dict={}
ind=0
for y in first_years:
    y=int(y)
    temp='ret_alldata_year_'+str(start_years[ind])
    exec(f"{temp}=ret_12_months[((ret_12_months['Year'] == y) & (ret_12_months['Months']>=4)) | ((ret_12_months['Year']==y+1) & (ret_12_months['Months']<=3))].copy()")
    exec(f"{temp}.insert(1, 'Months_Name', get_month_name({temp}['Months']), True)")
    exec(f"{temp}={temp}.drop('Year',axis=1)")
    exec(f"{temp}={temp}.drop('Months',axis=1)")
#     print(temp.to_string())
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.imshow({temp}.set_index('Months_Name'),y={temp}['Months_Name'],width=800,height=800,color_continuous_scale=heatmap_color_scheme_low,text_auto=True)")
    exec(f"{temp_fig}.update_layout(margin=dict(l=0, r=0, t=200, b=100),title='Retention of {y}-{y+1} (Considering Complete Data)',title_font_size=24,xaxis_side='top')")
    eval(temp_fig).show()
    fig_dict[f"Year :{years[ind]}"]=[eval(temp_fig),eval(temp)]
    ind=ind+1
    
ret_dict[f"Retention of all years"]=fig_dict

In [318]:
main_fig_num=fig_num
print(main_fig_num)

229


In [319]:
title=f"Month-wise Retention Analysis"
fig_dict={}
i=0
fig_num=main_fig_num
for m in months:
    num=12
    temp='ret_all_'+str(m)
    exec(f"{temp}=pd.DataFrame()")
    
    for y in start_years[:-data_incomplete_year_count]:
        temp2='ret_alldata_year_'+str(y)
        exec(f"{temp2} = {temp2}.fillna(-1)")

        row = eval(temp2).iloc[i]
        row=row.iloc[1:]
        row=row.tolist()
        row = [value for value in row if not pd.isna(value)]
        row = [round(value, 1) for value in row]
        if eval(temp).empty:
            new_months = list(range(1,num+1))
            exec(f"{temp}=pd.DataFrame(columns=new_months)")
            exec(f"{temp}.loc[len({temp})] = row")
        else:
            exec(f"{temp}.loc[len({temp})] = row")
    eval(temp).insert(0, 'Year', short_years[:-data_incomplete_year_count], True)
    exec(f"{temp} = {temp}.replace(-1,np.nan)")
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}=go.Figure()")
    exec(f"{temp_fig} = px.imshow(eval(temp).set_index('Year'), y=eval(temp)['Year'],color_continuous_scale=heatmap_color_scheme_low,text_auto=True)")
    exec(f"{temp_fig}.update_layout(margin=dict(t=200, b=100),title='{months[i]} Retention Analysis (Considering Complete Data)',title_font_size=24,xaxis_side='top')")
    eval(temp_fig).show()
    fig_dict[f"Month:{m}"]=[eval(temp_fig),eval(temp)]
    i=i+1
ret_dict[title]=fig_dict 

In [320]:
main_fig_num=fig_num
print(main_fig_num)

241


In [321]:
title=f"(Line) Retention Analysis"
fig_dict={}
i=0
fig_num=main_fig_num
for m in months:
    temp='ret_all_'+str(m)
    exec(f"{temp} = {temp}.replace(-1, pd.NaT)") #Replacing all -1 with NAN so that it does not get plot
    traces = []
    for i in range(len(eval(temp))):
        traces.append(go.Scatter(
            x=eval(temp).columns[1:], # Use the column names as x-axis values
            y=eval(temp).iloc[i, 1:], # Select the data values for the current row
            name=eval(temp)['Year'][i] # Use the Year column for the legend label
        ))

    # Define the plot layout
    layout = go.Layout(
        title=f"Retention Analysis of {m} (Considering Complete Data)",
        xaxis=dict(title='Months'),
        yaxis=dict(title='Customer Retained')
    )

    # Create the plot figure
    temp_fig='fig_'+str(fig_num)
    fig_num=fig_num+1;
    exec(f"{temp_fig}= go.Figure(data=traces, layout=layout)")
    print(eval(temp_fig).show())
    fig_dict[f"Month:{m}"]=[eval(temp_fig),eval(temp)]
    i=i+1
ret_dict[title]=fig_dict 

None


None


None


None


None


...

None


None


None


None


None


In [322]:
main_fig_num=fig_num
print(main_fig_num)

253


In [323]:
main_data_dict["Retention Analysis (Considering Complete Data)"]=ret_dict


In [324]:
# Cross Selling Recomendation
if cdict['ProductDetail'] and cdict['OrderID'] and cdict['Segment']:
    print(1)

1


In [325]:
# Creating a datacopy for working
csr=df.copy()

In [326]:
# # Renaming Column for working easily
# csr['OrderID']=df['Sales Order']
# csr['ProductDetail']=df['Description']

In [327]:
# Preprocessing the data
missing = csr.isna().sum()
csr=csr.dropna(subset=['ProductDetail'])
csr=csr.dropna(subset=['OrderID'])
# missing = csr.isna().sum()

In [328]:
# csr_g contain copy of csr for doing genral cross selling analysis
csr_g=csr.copy()

In [329]:
# Adding a product bundle column which will contain all the product under same orderID
csr=csr[csr['OrderID'].duplicated(keep=False)]
csr_g['ProductBundle']=csr_g.groupby(['OrderID'])['ProductDetail'].transform(lambda x: ','.join(x))
csr_g=csr_g[['OrderID','ProductBundle','Segment']].drop_duplicates()
csr_g

OrderID                                      ProductBundle   
0     CA-2017-152156  Bush Somerset Collection Bookcase,Hon Deluxe F...  \
2     CA-2017-138688  Self-Adhesive Address Labels for Typewriters b...   
3     US-2016-108966  Bretford CR4500 Series Slim Rectangular Table,...   
5     CA-2015-115812  Eldon Expressions Wood and Plastic Desk Access...   
12    CA-2018-114412                                         Xerox 1967   
...              ...                                                ...   
9786  US-2015-114377                Global Stack Chair with Arms, Black   
9787  CA-2018-144491  Atlantic Metals Mobile 5-Shelf Bookcases, Cust...   
9791  CA-2015-127166  Staple envelope,Global Deluxe Steno Chair,Adam...   
9795  CA-2017-125920  Cardinal HOLDit! Binder Insert Strips,Extra St...   
9796  CA-2016-128608  BIC Brite Liner Highlighters, Chisel Tip,GE 30...   

        Segment  
0      Consumer  
2     Corporate  
3      Consumer  
5      Consumer  
12     Consumer  
...         ...  
9786   Consumer  
9787   Consumer  
9791   Consumer  
9795  Corporate  
9796  Corporate  

[4922 rows x 3 columns]

In [330]:
# Here we create a counter and count the number of purchase of each combination
# of product and display the most common combination
count = Counter()
general_cross_sell={}
for row in csr_g['ProductBundle']:
    row_list=row.split(',')
    count.update(Counter(combinations(row_list,2)))
count=count.most_common(10)

i=0
for key in count:
    if key[0][0]!=key[0][1]:
        print(key)
    else:
        key=[]

general_cross_sell['General'] = pd.DataFrame([{'Product 1': t[0][0], 'Product 2': t[0][1], 'Count': t[1]} for t in count])
cross_sell_dict['General']=general_cross_sell

(('Acco Pressboard Covers with Storage Hooks', ' 14 7/8" x 11"'), 24)
(('Acco Pressboard Covers with Storage Hooks', ' Executive Red'), 17)
(('Adams Telephone Message Book W/Dividers/Space For Phone Numbers', ' 5 1/4"X8 1/2"'), 17)
((' Chisel Tip', ' Yellow'), 15)
(('Situations Contoured Folding Chairs', ' 4/Set'), 15)
(('Global High-Back Leather Tilter', ' Burgundy'), 14)
(("Global Wood Trimmed Manager's Task Chair", ' Khaki'), 14)
(('Global Leather Highback Executive Chair with Pneumatic Height Adjustment', ' Black'), 13)
(('Hot File 7-Pocket', ' Floor Stand'), 13)
(('ACCOHIDE 3-Ring Binder', ' Blue'), 13)


In [331]:
# Segment wise Cross Selling

In [332]:
csr_seg=csr.copy()
csr_seg=csr_seg.dropna(subset=['Segment'])
csr_seg=csr_seg[csr_seg['OrderID'].duplicated(keep=False)]
csr_seg['ProductBundle']=csr_seg.groupby(['OrderID','Segment'])['ProductDetail'].transform(lambda x: ','.join(x))
csr_seg=csr_seg[['OrderID','ProductBundle','Segment']].drop_duplicates()
new_segments=csr_seg['Segment'].unique()
segment_cross_sell={}
for seg in new_segments:
    count = Counter()
    csr_new=csr_seg[csr_seg['Segment']==seg].copy()
    for row in csr_new['ProductBundle']:
        row_list=row.split(',')
        count.update(Counter(combinations(row_list,2)))
    count=count.most_common(10)
    i=0
    print("\n\nSegment : ",seg)
    for key in count:
        if key[0][0]!=key[0][1]:
              print(key)
    segment_cross_sell[seg] = pd.DataFrame([{'Product 1': t[0][0], 'Product 2': t[0][1], 'Count': t[1]} for t in count])
cross_sell_dict['Segment']=segment_cross_sell



Segment :  Consumer
((' Chisel Tip', ' Yellow'), 7)
(('Angle-D Binders with Locking Rings', ' Label Holders'), 7)
(('Hot File 7-Pocket', ' Floor Stand'), 7)
(('Hon Deluxe Fabric Upholstered Stacking Chairs', ' Rounded Back'), 6)
(('Wilson Jones Hanging View Binder', ' White'), 6)
(('Wilson Jones Hanging View Binder', ' 1"'), 6)
((' White', ' 1"'), 6)
(('Acco Pressboard Covers with Storage Hooks', ' Executive Red'), 6)
(('Global Leather Task Chair', ' Black'), 6)
(('Tyvek  Top-Opening Peel & Seel Envelopes', ' Plain White'), 6)


Segment :  Home Office
(('Adams Telephone Message Book W/Dividers/Space For Phone Numbers', ' 5 1/4"X8 1/2"'), 4)
(('Global Leather Highback Executive Chair with Pneumatic Height Adjustment', ' Black'), 4)
(('Acco Pressboard Covers with Storage Hooks', ' 14 7/8" x 11"'), 4)
(('Acco Pressboard Covers with Storage Hooks', ' Executive Red'), 4)
((' 14 7/8" x 11"', ' Executive Red'), 4)
(('Chromcraft Bull-Nose Wood Round Conference Table Top', ' Wood Base'), 3)
(

In [333]:
# State wise Cross Selling
if cdict['ProductDetail'] and cdict['OrderID'] and cdict['ProductDetail']:
    print(1)

1


In [334]:
csr_state=csr.copy()
missing = csr_state.isna().sum()
csr_state=csr_state.dropna(subset=['State'])
csr_state=csr_state[csr_state['OrderID'].duplicated(keep=False)]
csr_state['ProductBundle']=csr_state.groupby(['OrderID','State'])['ProductDetail'].transform(lambda x: ','.join(x))
csr_state=csr_state[['OrderID','ProductBundle','State']].drop_duplicates()
new_states=csr_state['State'].unique()
state_cross_sell={}
for st in new_states:
    count = Counter()
    csr_new=csr_state[csr_state['State']==st].copy()
    for row in csr_new['ProductBundle']:
        row_list=row.split(',')
        count.update(Counter(combinations(row_list,2)))
    count=count.most_common(10)
    i=0
    print("\n\nState : ",st)
    for key in count:
        if key[0][0]!=key[0][1]:
              print(key)
    state_cross_sell[st] = pd.DataFrame([{'Product 1': t[0][0], 'Product 2': t[0][1], 'Count': t[1]} for t in count])
cross_sell_dict['State']=state_cross_sell



State :  Kentucky
(('GBC Prepunched Paper', ' 19-Hole'), 3)
(('GBC Prepunched Paper', ' for Binding Systems'), 3)
(('GBC Prepunched Paper', ' 24-lb'), 3)
((' 19-Hole', ' for Binding Systems'), 3)
((' 19-Hole', ' 24-lb'), 3)
((' for Binding Systems', ' 24-lb'), 3)
(('Hon Deluxe Fabric Upholstered Stacking Chairs', ' Rounded Back'), 2)
(('Eldon Expressions Wood and Plastic Desk Accessories', 'GBC Prepunched Paper'), 2)
(('Eldon Expressions Wood and Plastic Desk Accessories', ' 19-Hole'), 2)
(('Eldon Expressions Wood and Plastic Desk Accessories', ' for Binding Systems'), 2)


State :  Florida
(('Acco 7-Outlet Masterpiece Power Center', ' Wihtout Fax/Phone Line Protection'), 2)
(('Eldon Expressions Desk Accessory', ' Wood Photo Frame'), 2)
(('Eldon Expressions Desk Accessory', ' Mahogany'), 2)
((' Wood Photo Frame', ' Mahogany'), 2)
(('Decoflex Hanging Personal Folder File', ' Blue'), 2)
(('Bretford CR4500 Series Slim Rectangular Table', "Eldon Fold 'N Roll Cart System"), 1)
(('Bush Adv

In [335]:
main_data_dict["Cross Selling"]=cross_sell_dict

In [336]:
for key,value in main_data_dict.items():
    print(f"1 = Key:{key}    Value:{type(value)}\n")
    for k,v in value.items():
        print(f"   2 = Key:{k}    Value:{type(v)}\n")
        for nk,nv in v.items():
            print(f"      3 = Key:{nk}    Value:{type(nv)}\n")

1 = Key:Overall Analysis    Value:<class 'dict'>

   2 = Key:Revenue of Each Year    Value:<class 'dict'>

      3 = Key:Total    Value:<class 'list'>

   2 = Key:Revenue Per Month Of Each Year    Value:<class 'dict'>

      3 = Key:Year    Value:<class 'list'>

   2 = Key:Revenue Per Quarter of Each Year    Value:<class 'dict'>

      3 = Key:Quarter    Value:<class 'list'>

1 = Key:State Analysis    Value:<class 'dict'>

   2 = Key:Revenue per State    Value:<class 'dict'>

      3 = Key:Total    Value:<class 'list'>

   2 = Key:Revenue Per State of Each Year    Value:<class 'dict'>

      3 = Key:Year    Value:<class 'list'>

   2 = Key:Revenue Per State of Each Quarter    Value:<class 'dict'>

      3 = Key:Quarter    Value:<class 'list'>

   2 = Key:Revenue Per State Of Each Quarter For Each Year    Value:<class 'dict'>

      3 = Key:Year:14    Value:<class 'list'>

      3 = Key:Year:15    Value:<class 'list'>

      3 = Key:Year:16    Value:<class 'list'>

      3 = Key:Year:17

In [337]:
# Creating Pickle File
# This will store our dictionary with all the plots and other dataframe in pichkle file which can be used to make dashboard

In [338]:
with open('assets/Figure.pickle', 'wb') as f:
    pickle.dump(main_data_dict, f)
